###  Function to mount to criteosmall public dataset bucket

In [2]:
def mount_s3_bucket(access_key, secret_key, bucket_name, mount_folder):
  ACCESS_KEY_ID = access_key
  SECRET_ACCESS_KEY = secret_key
  ENCODED_SECRET_KEY = SECRET_ACCESS_KEY.replace("/", "%2F")

  print ("Mounting", bucket_name)

  try:
    # Unmount the data in case it was already mounted.
    dbutils.fs.unmount("/mnt/%s" % mount_folder)
    
  except:
    # If it fails to unmount it most likely wasn't mounted in the first place
    print ("Directory not unmounted: ", mount_folder)
    
  finally:
    # Lastly, mount our bucket.
    dbutils.fs.mount("s3a://%s:%s@%s" % (ACCESS_KEY_ID, ENCODED_SECRET_KEY, bucket_name), "/mnt/%s" % mount_folder)
    #dbutils.fs.mount("s3a://"+ ACCESS_KEY_ID + ":" + ENCODED_SECRET_KEY + "@" + bucket_name, mount_folder)
    print ("The bucket", bucket_name, "was mounted to", mount_folder, "\n")

###  Set your access key and secret access key
> <br>

In [4]:
# Set AWS programmatic access credentials
ACCESS_KEY = ""
SECRET_ACCESS_KEY = ""

### Mount the datasets required for this course
> <br>
> * It may take 5-10 minutes. The mounting process is slow.

#### Mounting

In [7]:
from pyspark.sql import SparkSession
spark = SparkSession \
        .builder \
        .appName('WeCloud Spark Training') \
        .getOrCreate()
print('Session created')

Session created

In [8]:
sc = spark.sparkContext

In [9]:
criteoDF.rdd.glom().take(5)[:][0:1]

In [10]:
mount_s3_bucket(ACCESS_KEY, SECRET_ACCESS_KEY, "criteo-small", "criteo-small")

Mounting criteo-small
Directory not unmounted: criteo-small
The bucket criteo-small was mounted to criteo-small

In [11]:
%fs
ls /mnt/criteo-small

path name size dbfs:/mnt/criteo-small/train.tsv.gz train.tsv.gz 4044433407

### Reading the Criteo Dataset (Tab Seperated File)

##### Creating a Schema

In [14]:
# creating my own shema
criteoFiles = "/mnt/criteo-small/train.tsv.gz"


from pyspark.sql.types import StructType, StructField, IntegerType, StringType, BooleanType

criteoSchema = StructType([
    StructField("label", IntegerType(), True),
    StructField("i_1", IntegerType(), True),
    StructField("i_2", IntegerType(), True),
    StructField("i_3", IntegerType(), True),
    StructField("i_4", IntegerType(), True),
    StructField("i_5", IntegerType(), True),
    StructField("i_6", IntegerType(), True),
    StructField("i_7", IntegerType(), True),
    StructField("i_8", IntegerType(), True),
    StructField("i_9", IntegerType(), True),
    StructField("i_10", IntegerType(), True),
    StructField("i_11", IntegerType(), True),
    StructField("i_12", IntegerType(), True),
    StructField("i_13", IntegerType(), True),
    StructField("c_1", StringType(), True),
    StructField("c_2", StringType(), True),
    StructField("c_3", StringType(), True),
    StructField("c_4", StringType(), True),
    StructField("c_5", StringType(), True),
    StructField("c_6", StringType(), True),
    StructField("c_7", StringType(), True),
    StructField("c_8", StringType(), True), StructField("c_9", StringType(), True), StructField("c_10", StringType(), True), StructField("c_11", StringType(), True), StructField("c_12", StringType(), True), StructField("c_13", StringType(), True), StructField("c_14", StringType(), True), StructField("c_15", StringType(), True), StructField("c_16", StringType(), True), StructField("c_17", StringType(), True), StructField("c_18", StringType(), True), StructField("c_19", StringType(), True), StructField("c_20", StringType(), True), StructField("c_21", StringType(), True), StructField("c_22", StringType(), True), StructField("c_23", StringType(), True), StructField("c_24", StringType(), True), StructField("c_25", StringType(), True),StructField("c_26", StringType(), True)
]
)



##### Reading the Tab Seperated File

In [16]:
criteoSmallDF = (spark.read
    .option("header", "false")
    .option("delimiter", "\t")
    .schema(criteoSchema)
    .csv(criteoFiles)
)

In [17]:
criteoSmallDF.printSchema()

root
-- label: integer (nullable = true)
-- i_1: integer (nullable = true)
-- i_2: integer (nullable = true)
-- i_3: integer (nullable = true)
-- i_4: integer (nullable = true)
-- i_5: integer (nullable = true)
-- i_6: integer (nullable = true)
-- i_7: integer (nullable = true)
-- i_8: integer (nullable = true)
-- i_9: integer (nullable = true)
-- i_10: integer (nullable = true)
-- i_11: integer (nullable = true)
-- i_12: integer (nullable = true)
-- i_13: integer (nullable = true)
-- c_1: string (nullable = true)
-- c_2: string (nullable = true)
-- c_3: string (nullable = true)
-- c_4: string (nullable = true)
-- c_5: string (nullable = true)
-- c_6: string (nullable = true)
-- c_7: string (nullable = true)
-- c_8: string (nullable = true)
-- c_9: string (nullable = true)
-- c_10: string (nullable = true)
-- c_11: string (nullable = true)
-- c_12: string (nullable = true)
-- c_13: string (nullable = true)
-- c_14: string (nullable = true)
-- c_15: string (nullable = true)
-- c_16: string (nullable = true)
-- c_17: string (nullable = true)
-- c_18: string (nullable = true)
-- c_19: string (nullable = true)
-- c_20: string (nullable = true)
-- c_21: string (nullable = true)
-- c_22: string (nullable = true)
-- c_23: string (nullable = true)
-- c_24: string (nullable = true)
-- c_25: string (nullable = true)
-- c_26: string (nullable = true)

In [18]:
criteoSmallDF.count()

Out[10]: 45840617

In [19]:
#count the number of clicked on adds and the number of non clicked on adds
#the data is highly unbalanced, the number of clicked on adds is only approximately 26% of the data while 74% of the data represents unclicked on adds

criteoSmallDF.groupBy('label').count().orderBy('label').show()

+-----+--------+
label| count|
+-----+--------+
 0|34095179|
 1|11745438|
+-----+--------+

### Write the Criteo Dataset as a Parquet File

In [21]:
# save the file as parquet file

criteoOutParquet = "/tmp/criteo_small.parquet"

(criteoSmallDF.write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "snappy")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoOutParquet)               # Write DataFrame to parquet files
)

### Read the Parquet file

In [23]:
# Read the parquet file
criteoOutParquet = "/tmp/criteo_small.parquet"

criteo_small_Parquet_DF = (spark.read              
  .option("delimiter", "\t")  
  .schema(criteoSchema)        # Use the specified schema
  .parquet(criteoOutParquet)   # Creates a DataFrame from Parquet after reading in the file
)

In [24]:
# Count the number of clicked on adds versus non clicked on adds
criteo_small_Parquet_DF.groupBy('label').count().orderBy('label').show()

+-----+--------+
label| count|
+-----+--------+
 0|34095179|
 1|11745438|
+-----+--------+

### Count null values in each coulmn
> <br>

In [26]:
# Count the number of nulls in each coulmn regardless of the label and showing the percentage of nulls

from pyspark.sql.functions import count, col
columns= criteo_small_Parquet_DF.columns[1:]
critieo_null_percentage=dict()
for i in columns:
  critieo_null_percentage[i]=criteo_small_Parquet_DF.filter(col(i).isNull()).count() / criteo_small_Parquet_DF.count()
print(critieo_null_percentage)



{'i_1': 0.45360550011794126, 'i_2': 0.0, 'i_3': 0.2146447330759095, 'i_4': 0.2167808736082239, 'i_5': 0.02580936028849699, 'i_6': 0.2236516144623446, 'i_7': 0.04325565687739325, 'i_8': 0.000496786507040252, 'i_9': 0.04325565687739325, 'i_10': 0.45360550011794126, 'i_11': 0.04325565687739325, 'i_12': 0.7650780965709951, 'i_13': 0.2167808736082239, 'c_1': 0.0, 'c_2': 0.0, 'c_3': 0.03401945920579559, 'c_4': 0.03401945920579559, 'c_5': 0.0, 'c_6': 0.12086715586747011, 'c_7': 0.0, 'c_8': 0.0, 'c_9': 0.0, 'c_10': 0.0, 'c_11': 0.0, 'c_12': 0.03401945920579559, 'c_13': 0.0, 'c_14': 0.0, 'c_15': 0.0, 'c_16': 0.03401945920579559, 'c_17': 0.0, 'c_18': 0.0, 'c_19': 0.4400651500829494, 'c_20': 0.4400651500829494, 'c_21': 0.03401945920579559, 'c_22': 0.7625349588990044, 'c_23': 0.0, 'c_24': 0.03401945920579559, 'c_25': 0.4400651500829494, 'c_26': 0.4400651500829494}

### Display the null counts for each coulmn ordered descending
> <br>

In [28]:
# 15 attributes have no null values, 2 have more than 75% and 6 between 44% and 45% and 16 >0 and less than 44%
sort_critieo_null_percentage = sorted(critieo_null_percentage.items(), key=lambda x: x[1], reverse=True)
for item in sort_critieo_null_percentage:
  print(item)

('i_12', 0.7650780965709951)
('c_22', 0.7625349588990044)
('i_1', 0.45360550011794126)
('i_10', 0.45360550011794126)
('c_19', 0.4400651500829494)
('c_20', 0.4400651500829494)
('c_25', 0.4400651500829494)
('c_26', 0.4400651500829494)
('i_6', 0.2236516144623446)
('i_4', 0.2167808736082239)
('i_13', 0.2167808736082239)
('i_3', 0.2146447330759095)
('c_6', 0.12086715586747011)
('i_7', 0.04325565687739325)
('i_9', 0.04325565687739325)
('i_11', 0.04325565687739325)
('c_3', 0.03401945920579559)
('c_4', 0.03401945920579559)
('c_12', 0.03401945920579559)
('c_16', 0.03401945920579559)
('c_21', 0.03401945920579559)
('c_24', 0.03401945920579559)
('i_5', 0.02580936028849699)
('i_8', 0.000496786507040252)
('i_2', 0.0)
('c_1', 0.0)
('c_2', 0.0)
('c_5', 0.0)
('c_7', 0.0)
('c_8', 0.0)
('c_9', 0.0)
('c_10', 0.0)
('c_11', 0.0)
('c_13', 0.0)
('c_14', 0.0)
('c_15', 0.0)
('c_17', 0.0)
('c_18', 0.0)
('c_23', 0.0)

### Filter the Coulmns where Null Percentage Is More Than 40%
> <br>

In [30]:
# Filter the coulmns that have null values more than 40% of their values
coulmns_to_drop=[] # coulmns to be dropped
coulmns_to_convert_to_Bool=[] # columns to convert to boolean value (True/False)
for col in critieo_null_percentage:
  if critieo_null_percentage[col] > 0.40:
    print (col, ":",critieo_null_percentage[col]) # print all the coulmn names that have more than 40% nulls
    if critieo_null_percentage[col] > 0.70:
      coulmns_to_drop.append(col)
    else:
      coulmns_to_convert_to_Bool.append(col)
    

i_1 : 0.45360550011794126
i_10 : 0.45360550011794126
i_12 : 0.7650780965709951
c_19 : 0.4400651500829494
c_20 : 0.4400651500829494
c_22 : 0.7625349588990044
c_25 : 0.4400651500829494
c_26 : 0.4400651500829494

### Dispaly the Coulmn Names That Will Be Dropped
> <br>

In [32]:
print(coulmns_to_drop)

['i_12', 'c_22']

### Dispaly the Coulmn names that will be Transformed to Boolean
> <br>

In [34]:
print(coulmns_to_convert_to_Bool)

['i_1', 'i_10', 'c_19', 'c_20', 'c_25', 'c_26']

### Balance The Data
> <br>

In [36]:
# Creating a balanced dataset
# filtering the rows into two sets clicked on adds and unclicked on adds
# from the parquet file
from pyspark.sql.functions import col
critieo_clicked=criteo_small_Parquet_DF.filter(col("label")==1)
critieo_unclicked=criteo_small_Parquet_DF.filter(col("label")==0)

      

In [37]:
# Select from the unclicked sample approximately 11745438 random records which are the number of 
# records avaialble in the data where label =1 (clicked on adds)
critieo_unclicked=critieo_unclicked.sample(False, 0.34448, 100)


In [38]:
critieo_unclicked.count()

Out[19]: 11745671

In [39]:
critieo_clicked.count()

Out[20]: 11745438

In [40]:
# Combine the two dataframes  critieo_clicked and critieo_unclicked and put them back in criteo_small_Parquet_DF
criteo_small_Parquet_DF=critieo_clicked.union(critieo_unclicked)

### Drop the coulmns where null count exceeds 75%
> <br>

In [42]:
# Before replacing the integer valued columns with the mean and the categorical values with the mode
# I would like to drop the coulmns that have more than 70% null values
# these coulmns are i_12,c_22
# coulmns_to_drop=["i_12","c_22"]
criteo_small_Parquet_DF=criteo_small_Parquet_DF.drop(*coulmns_to_drop)
criteo_small_Parquet_DF.columns

Out[11]: ['label',
 'i_1',
 'i_2',
 'i_3',
 'i_4',
 'i_5',
 'i_6',
 'i_7',
 'i_8',
 'i_9',
 'i_10',
 'i_11',
 'i_13',
 'c_1',
 'c_2',
 'c_3',
 'c_4',
 'c_5',
 'c_6',
 'c_7',
 'c_8',
 'c_9',
 'c_10',
 'c_11',
 'c_12',
 'c_13',
 'c_14',
 'c_15',
 'c_16',
 'c_17',
 'c_18',
 'c_19',
 'c_20',
 'c_21',
 'c_23',
 'c_24',
 'c_25',
 'c_26']

In [43]:
display(criteo_small_Parquet_DF)

label i_1 i_2 i_3 i_4 i_5 i_6 i_7 i_8 i_9 i_10 i_11 i_13 c_1 c_2 c_3 c_4 c_5 c_6 c_7 c_8 c_9 c_10 c_11 c_12 c_13 c_14 c_15 c_16 c_17 c_18 c_19 c_20 c_21 c_23 c_24 c_25 c_26 1 1 4 2 0 0 0 1 0 0 1 1 0 68fd1e64 2c16a946 503b9dbc e4dbea90 f3474129 13718bbd 38eb9cf4 1f89b562 a73ee510 547c0ffe bc8c9f21 60ab2f07 46f42a63 07d13a8f 18231224 e6b6bdc7 e5ba7672 74ef3502 null null 5316a17f 32c7478e 9117a34a null null 1 0 -1 null null 1465 0 17 0 4 0 4 null 241546e0 38a947a1 fa673455 6a14f9b9 25c83c98 fe6b92e5 1c86e0eb 1f89b562 a73ee510 e7ba2569 755e4a50 208d9687 5978055e 07d13a8f 5182f694 f8b34416 e5ba7672 e5f8f18f null null f3ddd519 32c7478e b34f3128 null null 1 null 2 11 5 10262 34 2 4 5 null 1 5 be589b51 287130e0 cd7a7a22 fb7334df 25c83c98 null 6cdb3998 361384ce a73ee510 3ff10fb2 5874c9c9 976cbd4c 740c210d 1adce6ef 310d155b 07eb8110 07c540c4 891589e7 18259a83 a458ea53 a0ab60ca 32c7478e a052b1ed 9b3e8820 8967c0d2 1 1 987 null 2 105 2 1 2 2 1 1 2 68fd1e64 38d50e09 da603082 431a5096 43b19349 7e0ccccf 3f35b640 0b153874 a73ee510 3b08e48b 3d5fb018 6aaab577 94172618 07d13a8f ee569ce2 2f03ef40 d4bb7bd8 582152eb 21ddcdc9 b1252a9d 3b203ca1 32c7478e b21dc903 001f3601 aa5f0a15 1 null 47 null 0 6399 38 19 10 143 null 10 6 1464facd 38a947a1 223b0e16 ca55061c 25c83c98 7e0ccccf 6933dec1 5b392875 a73ee510 3b08e48b 860c302b 156f99ef 30735474 1adce6ef 0e78291e 5fbf4a84 e5ba7672 1999bae9 null null deb9605d 32c7478e e448275f null null 1 0 1 20 16 1548 93 42 32 912 0 15 16 8cf07265 942f9a8d a8e40bcf 0365276a 25c83c98 7e0ccccf 3f4ec687 1f89b562 a73ee510 726f00fd c4adf918 27c604a6 85dbe138 07d13a8f a8e962af c449f783 27c07bd6 1f868fdd 21ddcdc9 a458ea53 7eee76d1 32c7478e 9af06ad9 9d93af03 cdfe5ab7 1 0 20 2 2 7188 170 2 3 24 0 2 2 68fd1e64 38a947a1 ee6e4611 30d9fc77 4cf72387 7e0ccccf bf9d4f90 0b153874 a73ee510 b7c4dad5 81cae03e 5332e3fb d413ef3e 07d13a8f a6d97bf2 ec676ace 3486227d 02e8d897 null null b055c31b 3a171ecb ae2cd100 null null 1 0 78 2 15 4311 85 4 18 230 0 3 15 68fd1e64 1287a654 5ed035c9 5b5365b2 4cf72387 6f6d9be8 1b1aa9ea 0b153874 a73ee510 c3e69838 7a3651f5 df8b1dea 95bc260c b28479f6 ced5be3a 4cc0abe4 e5ba7672 df00d249 null null f520f961 32c7478e 27b60b01 null null 1 3 0 4 13 224 28 3 35 27 1 1 13 05db9164 90081f33 993f507e 14a74146 25c83c98 13718bbd dc7659bd 0b153874 a73ee510 03e48276 e51ddf94 18fe7085 3516f6e6 64c94865 98995c3b 8c48eb08 e5ba7672 7181ccc8 null null 2ed6b316 3a171ecb abf08f1b null null 1 null 277 null 3 7318 24 6 3 98 null 1 3 8cf07265 9adf4cf9 2e76fb61 0b1ad9da 4cf72387 fe6b92e5 75dcaaca 0b153874 a73ee510 3b08e48b 8aabdae8 9886a0a7 edcf17ce 07d13a8f 2aaebd23 338c0d09 e5ba7672 c7dbecd5 null null 60d2d691 3a171ecb 90b6276f null null 1 1 259 1 1 5 1 6 1 1 1 3 1 05db9164 f3b07830 ad981000 f96c819d 25c83c98 null df5c2d18 0b153874 a73ee510 8aef4905 a7b606c4 b912be9f eae197fd b28479f6 d27eed0e b8b09fe6 e5ba7672 048d01f4 null null 08ae854d 32c7478e c657e6e5 null null 1 0 127 1 3 1683 19 26 17 475 0 9 3 05db9164 8947f767 11c9d79e 52a787c8 4cf72387 fbad5c96 18671b18 0b153874 a73ee510 ceb10289 77212bd7 79507c6b 7203f04e 07d13a8f 2c14c412 49013ffe 8efede7f bd17c3da f6a3e43b a458ea53 35cd95c9 c7dc6720 3fdb382b 010f6491 49d68486 1 88 319 null 4 5 4 89 40 88 3 4 4 05db9164 08d6d899 333440d5 fc86bde0 25c83c98 fbad5c96 f00bddf8 0b153874 a73ee510 83ff688a 55795b33 1b0c8aa3 39795005 b28479f6 bffbd637 4a838997 8efede7f bbf70d82 null null 16e2e3b3 32c7478e d859b4dd null null 1 1 30 null 3 116 31 1 3 3 1 1 3 5a9ed9b0 38a947a1 0f90b6d6 16b922ed 25c83c98 fbad5c96 17b47bf9 0b153874 a73ee510 3b08e48b 76120d9d ee2d3fdb d4384424 07d13a8f 3046a70a 81371cbc d4bb7bd8 1bae7658 null null 37bad455 3a171ecb 9d96bacb null null 1 null 0 55 5 14477 null 0 5 1 null 0 5 05db9164 09e68b86 2beedeb2 c59396e7 25c83c98 7e0ccccf a972360e 0b153874 7cc72ec2 acf0058d 9e511730 8f70e33a 04e4a7e0 64c94865 91126f30 6df0eed9 e5ba7672 5aed7436 55dd3565 5840adea c412f773 3a171ecb 3fdb382b e8b83407 ccc71a58 1 null 1 7 3 10087 67 6 3 57 null 3 3 05db9164 d7988e72 fb535e16 6fe3d332 25c83c98 1

### Initialize the stages list for the pipeline
> <br>

In [45]:
stages = [] # stages in our Pipeline or transformations in dataset

### Transform the coulmns that have between 40% - 70% null values into boolean features
> <br>

In [47]:
from pyspark.ml.pipeline import Transformer
from pyspark.ml.param.shared import HasInputCol, HasOutputCol, Param
from pyspark.sql.functions import col, expr, when
from pyspark.sql import functions as F
from pyspark import keyword_only


### Custom Transformer for Converting some Coulmns that have more than 70% nulls into a Boolean Data Type


> <br>

In [49]:
# Custom Transformer for converting some coulmns into boolean
class TransformIntoBoolean(Transformer, HasInputCol, HasOutputCol):
  
  @keyword_only
  def __init__(self, inputCol=None, outputCol=None):
    super(TransformIntoBoolean, self).__init__()
    kwargs = self._input_kwargs
    self.setParams(**kwargs)
     
  @keyword_only
  def setParams(self, inputCol=None, outputCol=None):
      """Get params."""
      kwargs = self._input_kwargs
      return self._set(**kwargs)  
    
  def _transform(self, dataframe):
    out_col = self.getOutputCol()
    in_col = dataframe[self.getInputCol()]
    return (dataframe
              .withColumn(out_col, (F.when(in_col.isNull() , False)
                                .otherwise(True))))


In [50]:
# Adding Transformers for Converting Columns into Boolean to stages
for cl in coulmns_to_convert_to_Bool:
  transformToBoolean = TransformIntoBoolean(inputCol=cl, outputCol=cl)
  stages += [transformToBoolean]

In [51]:
# Testing the TransformIntoBoolean custom transformer on column "i_1"
from pyspark.ml import Pipeline
transformToBooleanTest = TransformIntoBoolean(inputCol="i_1", outputCol="i_1_bool")
bool_pipeline = Pipeline(stages=[transformToBooleanTest])
bool_pipeline_model = bool_pipeline.fit(criteo_small_Parquet_DF)
data = bool_pipeline_model.transform(criteo_small_Parquet_DF)
display(data.select(["i_1","i_1_bool"]))

i_1 i_1_bool 1 true 0 true null false 1 true null false 0 true 0 true 0 true 3 true null false 1 true 0 true 88 true 1 true null false null false null false null false 2 true 6 true null false null false null false 0 true 0 true 2 true null false 0 true null false 1 true 5 true 7 true 5 true null false 1 true 1 true 6 true 4 true 3 true 2 true 10 true 82 true 3 true null false 16 true null false 1 true 0 true null false 0 true 9 true 31 true 0 true 0 true null false 2 true 0 true 6 true 2 true 20 true 2 true null false null false 2 true 0 true null false null false 30 true 0 true 3 true 0 true null false 4 true 88 true 0 true 1 true 0 true null false 6 true 4 true 0 true 0 true 1 true null false 9 true null false 1 true null false 12 true null false 6 true 70 true 4 true null false null false 1 true 0 true 1 true 0 true null false 1 true null false 0 true 1 true 0 true 0 true 0 true 1 true 24 true 0 true 3 true 3 true null false 1 true 3 true null false null false null false 0 true 3 true 0 true 0 true 0 true null false null false null false null false 1 true null false 1 true 0 true 3 true null false null false 2 true null false null false null false null false null false null false null false 1 true 15 true null false null false null false null false null false 1 true null false 7 true 13 true 17 true null false 0 true 30 true 8 true 30 true null false null false 0 true null false 30 true 1 true null false 4 true null false 0 true 0 true 3 true 6 true 0 true 29 true null false 24 true null false null false 3 true null false 2 true 6 true 0 true null false null false 4 true null false 2 true 6 true 6 true null false 0 true 6 true 2 true 6 true 0 true 3 true 26 true 0 true 1 true null false 25 true null false 0 true 0 true 19 true 5 true null false 5 true null false 35 true 0 true null false 1 true 2 true null false 5 true null false null false 13 true 3 true null false null false 3 true 0 true 7 true 2 true 2 true 0 true null false null false null false 0 true 2 true 0 true 13 true 4 true 3 true 10 true 1 true 3 true 13 true null false 10 true 0 true null false 41 true 2 true null false null false null false 2 true 8 true 10 true 0 true null false null false 5 true 0 true 1 true null false 8 true 3 true null false 3 true 1 true 8 true null false 15 true 2 true null false null false 0 true 0 true 2 true 2 true 1 true 0 true 0 true 33 true 11 true null false null false 1 true 2 true null false 1 true 0 true null false 0 true 22 true null false null false 12 true 5 true 20 true 0 true 0 true 7 true 5 true null false 3 true null false 3 true 0 true null false null false 0 true 3 true 4 true 4 true null false 0 true 0 true 0 true 0 true 2 true 0 true 6 true 0 true 0 true null false 0 true 1 true 7 true 0 true 4 true 1 true null false 0 true 5 true null false null false null false null false 1 true 1 true 13 true null false 0 true 39 true 2 true 2 true 0 true 1 true null false 1 true 4 true 23 true 1 true 0 true 0 true 1 true null false 6 true 0 true null false 7 true 0 true 4 true 0 true null false null false 0 true 5 true 2 true null false null false 6 true 0 true 0 true 4 true null false 4 true 1 true null false 10 true 10 true null false 0 true 0 true 0 true null false 5 true null false null false 3 true 0 true 2 true 3 true null false 0 true 17 true 5 true 3 true 0 true 0 true null false 1 true 5 true 1 true 1 true 0 true 0 true null false null false 0 true 2 true 1 true null false 0 true null false 0 true null false 6 true null false 27 true null false 2 true null false null false 0 true null false 13 true null false 0 true 0 true 0 true 10 true 4 true 0 true 0 true 12 true 3 true 7 true 2 true 1 true 10 true 10 true 0 true 4 true 0 true 0 true 3 true 0 true 0 true 4 true null false 1 true null false 0 true 2 true null false 1 true null false 0 true null false null false 2 true 4 true 3 true null false null false 1 true 0 true 0 true 0 true 1 true 0 true null false null false 0 true 7 true 0 true null false null false null fa

### Replace null values in the integer coulmns with the mean based on the label.
### Replace null values in the categorical coulmns with the mode based on the label.


> <br>

In [53]:
# Filtering the rows into two sets clicked on adds and unclicked on adds
# from the parquet file
from pyspark.sql.functions import col
critieo_clicked=criteo_small_Parquet_DF.filter(col("label")==1)
critieo_unclicked=criteo_small_Parquet_DF.filter(col("label")==0)

In [54]:
# Finding the mean for each coulmn twice once if the label is 1 and once when the label is 0
# Using the parquet file
# Adding the name of the coulmn as a key and the mean as the value in a dictionary mean_mode_clicked_d, mean_mode_unclicked_d
from pyspark.sql.functions import col, avg,mean
ci=["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
mean_mode_clicked_d=dict()
mean_mode_unclicked_d=dict()
for i in ci:
  mean_mode_clicked_d[i]=critieo_clicked.where(col(i).isNotNull()).select(mean(i)).first()[0] 
  mean_mode_unclicked_d[i]=critieo_unclicked.where(col(i).isNotNull()).select(mean(i)).first()[0] 

print(mean_mode_clicked_d)
print(mean_mode_unclicked_d)



{'i_2': 135.4843153571625, 'i_3': 36.35110630980616, 'i_4': 6.491825574536723, 'i_5': 9210.84617144628, 'i_6': 64.98783414546708, 'i_7': 25.631531884527966, 'i_8': 11.733192983376433, 'i_9': 113.13394186334529, 'i_11': 4.093748066934811, 'i_13': 5.9631126877500185}
{'i_2': 95.70724065061928, 'i_3': 23.92960843949336, 'i_4': 7.600443351827682, 'i_5': 21796.887076896302, 'i_6': 137.16348976964676, 'i_7': 13.06159185728511, 'i_8': 12.782644119360356, 'i_9': 103.65096289863389, 'i_11': 2.2526029754460692, 'i_13': 8.961150238166741}

In [55]:

# Finding the mode for each coulmn twice once if the label is 1 and once when the label is 0
# using the parquet file
# adding the name of the coulmn as a key and the mean as the value in a dictionary mean_mode_clicked_d, mean_mode_unclicked_d
from pyspark.sql.functions import col
cc=["c_1","c_2","c_3","c_4","c_5","c_6","c_7","c_8","c_9","c_10","c_11","c_12","c_13","c_14","c_15","c_16","c_17","c_18","c_21","c_23","c_24"] #categorical coulmns

for i in cc:
  mean_mode_clicked_d[i]=critieo_clicked.filter(col(i) !="Null").groupby(i).count().orderBy("count", ascending=False).first()[0]
  mean_mode_unclicked_d[i]=critieo_unclicked.filter(col(i) !="Null").groupby(i).count().orderBy("count", ascending=False).first()[0]
  
print(mean_mode_clicked_d)
print(mean_mode_unclicked_d)

{'i_2': 135.4843153571625, 'i_3': 36.35110630980616, 'i_4': 6.491825574536723, 'i_5': 9210.84617144628, 'i_6': 64.98783414546708, 'i_7': 25.631531884527966, 'i_8': 11.733192983376433, 'i_9': 113.13394186334529, 'i_11': 4.093748066934811, 'i_13': 5.9631126877500185, 'c_1': '05db9164', 'c_2': '38a947a1', 'c_3': 'd032c263', 'c_4': '13508380', 'c_5': '25c83c98', 'c_6': '7e0ccccf', 'c_7': '1c86e0eb', 'c_8': '0b153874', 'c_9': 'a73ee510', 'c_10': '3b08e48b', 'c_11': '755e4a50', 'c_12': '6aaba33c', 'c_13': '5978055e', 'c_14': '07d13a8f', 'c_15': '2d0bb053', 'c_16': 'b041b04a', 'c_17': 'e5ba7672', 'c_18': 'e88ffc9d', 'c_21': '723b4dfd', 'c_23': '32c7478e', 'c_24': 'b34f3128'}
{'i_2': 95.70724065061928, 'i_3': 23.92960843949336, 'i_4': 7.600443351827682, 'i_5': 21796.887076896302, 'i_6': 137.16348976964676, 'i_7': 13.06159185728511, 'i_8': 12.782644119360356, 'i_9': 103.65096289863389, 'i_11': 2.2526029754460692, 'i_13': 8.961150238166741, 'c_1': '05db9164', 'c_2': '38a947a1', 'c_3': 'd032c263', 'c_4': 'c18be181', 'c_5': '25c83c98', 'c_6': '7e0ccccf', 'c_7': '1c86e0eb', 'c_8': '0b153874', 'c_9': 'a73ee510', 'c_10': '3b08e48b', 'c_11': '755e4a50', 'c_12': 'dfbb09fb', 'c_13': '5978055e', 'c_14': 'b28479f6', 'c_15': '2d0bb053', 'c_16': '84898b2a', 'c_17': 'e5ba7672', 'c_18': 'e88ffc9d', 'c_21': '0014c32a', 'c_23': '32c7478e', 'c_24': '3fdb382b'}

### Custom Transformer for Replacing Null Values with Mean or Mode based on the Class Label 


> <br>

In [57]:
# Custom Transfromer for replacing null values with mean r mode based on the class label 

class ReplaceNullWithValue(Transformer, HasInputCol, HasOutputCol):
  
  @keyword_only
  def __init__(self, inputCol=None, outputCol=None,label = None , value1 = None, value2 = None):
      super(ReplaceNullWithValue, self).__init__()
      self.label = Param(self, "label", "Label coulmn of the data")
      self._setDefault(label="label")
      self.value1 = Param(self, "value1", "mean1 or mode1 for the coulmn where label =1")
      self.value2 = Param(self, "value2", "mean2 or mode2 for the coulmn where label =0")
      kwargs = self._input_kwargs
      self.setParams(**kwargs)
    
  @keyword_only
  def setParams(self, inputCol=None, outputCol=None,label = None , value1 = None, value2 = None):
      """Get params."""
      kwargs = self._input_kwargs
      print(kwargs)
      return self._set(**kwargs)  
  
  def setLabel(self, value):
      return self._set(label=value)

  def getLabel(self):
      return self.getOrDefault(self.label)

  def setValue1(self, value):
      return self._set(value1=value)

  def getValue1(self):
      return self.getOrDefault(self.value1)    

  def setValue2(self, value):
      return self._set(value2=value)

  def getValue2(self):
      return self.getOrDefault(self.value2)    
      
            
  def _transform(self, dataframe):
      out_col = self.getOutputCol()
      in_col = dataframe[self.getInputCol()]
      label_col = dataframe[self.getLabel()]
      return (dataframe.withColumn(out_col, 
                                   (F.when( ((in_col.isNull()) & (label_col == 1)) , self.getValue1()).
                                      when( ((in_col.isNull()) & (label_col == 0)) , self.getValue2()).otherwise(in_col))))

In [58]:
print(criteo_small_Parquet_DF.columns)

['label', 'i_1', 'i_2', 'i_3', 'i_4', 'i_5', 'i_6', 'i_7', 'i_8', 'i_9', 'i_10', 'i_11', 'i_13', 'c_1', 'c_2', 'c_3', 'c_4', 'c_5', 'c_6', 'c_7', 'c_8', 'c_9', 'c_10', 'c_11', 'c_12', 'c_13', 'c_14', 'c_15', 'c_16', 'c_17', 'c_18', 'c_19', 'c_20', 'c_21', 'c_23', 'c_24', 'c_25', 'c_26']

In [59]:
# Adding Transformers for replacing null values from categorical coulmns to mode

cc=["c_1","c_2","c_3","c_4","c_5","c_6","c_7","c_8","c_9","c_10","c_11","c_12","c_13","c_14","c_15","c_16","c_17","c_18","c_21","c_23","c_24"] #categorical coulmns
for cl in cc:
  replaceNullWithMode = ReplaceNullWithValue(inputCol=cl, outputCol=cl, label = "label", value1 = mean_mode_clicked_d[cl] ,value2 = mean_mode_unclicked_d[cl] )
  stages += [replaceNullWithMode]

{'inputCol': 'c_1', 'outputCol': 'c_1', 'label': 'label', 'value1': '05db9164', 'value2': '05db9164'}
{'inputCol': 'c_2', 'outputCol': 'c_2', 'label': 'label', 'value1': '38a947a1', 'value2': '38a947a1'}
{'inputCol': 'c_3', 'outputCol': 'c_3', 'label': 'label', 'value1': 'd032c263', 'value2': 'd032c263'}
{'inputCol': 'c_4', 'outputCol': 'c_4', 'label': 'label', 'value1': '13508380', 'value2': 'c18be181'}
{'inputCol': 'c_5', 'outputCol': 'c_5', 'label': 'label', 'value1': '25c83c98', 'value2': '25c83c98'}
{'inputCol': 'c_6', 'outputCol': 'c_6', 'label': 'label', 'value1': '7e0ccccf', 'value2': '7e0ccccf'}
{'inputCol': 'c_7', 'outputCol': 'c_7', 'label': 'label', 'value1': '1c86e0eb', 'value2': '1c86e0eb'}
{'inputCol': 'c_8', 'outputCol': 'c_8', 'label': 'label', 'value1': '0b153874', 'value2': '0b153874'}
{'inputCol': 'c_9', 'outputCol': 'c_9', 'label': 'label', 'value1': 'a73ee510', 'value2': 'a73ee510'}
{'inputCol': 'c_10', 'outputCol': 'c_10', 'label': 'label', 'value1': '3b08e48b', 'value2': '3b08e48b'}
{'inputCol': 'c_11', 'outputCol': 'c_11', 'label': 'label', 'value1': '755e4a50', 'value2': '755e4a50'}
{'inputCol': 'c_12', 'outputCol': 'c_12', 'label': 'label', 'value1': '6aaba33c', 'value2': 'dfbb09fb'}
{'inputCol': 'c_13', 'outputCol': 'c_13', 'label': 'label', 'value1': '5978055e', 'value2': '5978055e'}
{'inputCol': 'c_14', 'outputCol': 'c_14', 'label': 'label', 'value1': '07d13a8f', 'value2': 'b28479f6'}
{'inputCol': 'c_15', 'outputCol': 'c_15', 'label': 'label', 'value1': '2d0bb053', 'value2': '2d0bb053'}
{'inputCol': 'c_16', 'outputCol': 'c_16', 'label': 'label', 'value1': 'b041b04a', 'value2': '84898b2a'}
{'inputCol': 'c_17', 'outputCol': 'c_17', 'label': 'label', 'value1': 'e5ba7672', 'value2': 'e5ba7672'}
{'inputCol': 'c_18', 'outputCol': 'c_18', 'label': 'label', 'value1': 'e88ffc9d', 'value2': 'e88ffc9d'}
{'inputCol': 'c_21', 'outputCol': 'c_21', 'label': 'label', 'value1': '723b4dfd', 'value2': '0014c32a'}
{'inputCol': 'c_23', 'outputCol': 'c_23', 'label': 'label', 'value1': '32c7478e', 'value2': '32c7478e'}
{'inputCol': 'c_24', 'outputCol': 'c_24', 'label': 'label', 'value1': 'b34f3128', 'value2': '3fdb382b'}

In [60]:
# Adding Transformers for replacing null values from integer coulmns to mean

ci=["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
for cl in ci:
  replaceNullWithmean = ReplaceNullWithValue(inputCol=cl, outputCol=cl, label = "label", value1 = mean_mode_clicked_d[cl] ,value2 = mean_mode_unclicked_d[cl] )
  stages += [replaceNullWithmean]

{'inputCol': 'i_2', 'outputCol': 'i_2', 'label': 'label', 'value1': 135.4843153571625, 'value2': 95.70724065061928}
{'inputCol': 'i_3', 'outputCol': 'i_3', 'label': 'label', 'value1': 36.35110630980616, 'value2': 23.92960843949336}
{'inputCol': 'i_4', 'outputCol': 'i_4', 'label': 'label', 'value1': 6.491825574536723, 'value2': 7.600443351827682}
{'inputCol': 'i_5', 'outputCol': 'i_5', 'label': 'label', 'value1': 9210.84617144628, 'value2': 21796.887076896302}
{'inputCol': 'i_6', 'outputCol': 'i_6', 'label': 'label', 'value1': 64.98783414546708, 'value2': 137.16348976964676}
{'inputCol': 'i_7', 'outputCol': 'i_7', 'label': 'label', 'value1': 25.631531884527966, 'value2': 13.06159185728511}
{'inputCol': 'i_8', 'outputCol': 'i_8', 'label': 'label', 'value1': 11.733192983376433, 'value2': 12.782644119360356}
{'inputCol': 'i_9', 'outputCol': 'i_9', 'label': 'label', 'value1': 113.13394186334529, 'value2': 103.65096289863389}
{'inputCol': 'i_11', 'outputCol': 'i_11', 'label': 'label', 'value1': 4.093748066934811, 'value2': 2.2526029754460692}
{'inputCol': 'i_13', 'outputCol': 'i_13', 'label': 'label', 'value1': 5.9631126877500185, 'value2': 8.961150238166741}

In [61]:
# Testing the ReplaceNullWithMean custom transformer on column "i_2"
replaceNullWithMeanTest = ReplaceNullWithValue(inputCol="i_2", outputCol="i_2", label = "label", value1 = mean_mode_clicked_d["i_2"] ,value2 = mean_mode_unclicked_d["i_2"] )
mean_pipeline = Pipeline(stages=[replaceNullWithMeanTest])
mean_pipeline_model = mean_pipeline.fit(criteo_small_Parquet_DF)
data = mean_pipeline_model.transform(criteo_small_Parquet_DF)
display(data)

label i_1 i_2 i_3 i_4 i_5 i_6 i_7 i_8 i_9 i_10 i_11 i_13 c_1 c_2 c_3 c_4 c_5 c_6 c_7 c_8 c_9 c_10 c_11 c_12 c_13 c_14 c_15 c_16 c_17 c_18 c_19 c_20 c_21 c_23 c_24 c_25 c_26 1 1 4.0 2 0 0 0 1 0 0 1 1 0 68fd1e64 2c16a946 503b9dbc e4dbea90 f3474129 13718bbd 38eb9cf4 1f89b562 a73ee510 547c0ffe bc8c9f21 60ab2f07 46f42a63 07d13a8f 18231224 e6b6bdc7 e5ba7672 74ef3502 null null 5316a17f 32c7478e 9117a34a null null 1 0 -1.0 null null 1465 0 17 0 4 0 4 null 241546e0 38a947a1 fa673455 6a14f9b9 25c83c98 fe6b92e5 1c86e0eb 1f89b562 a73ee510 e7ba2569 755e4a50 208d9687 5978055e 07d13a8f 5182f694 f8b34416 e5ba7672 e5f8f18f null null f3ddd519 32c7478e b34f3128 null null 1 null 2.0 11 5 10262 34 2 4 5 null 1 5 be589b51 287130e0 cd7a7a22 fb7334df 25c83c98 null 6cdb3998 361384ce a73ee510 3ff10fb2 5874c9c9 976cbd4c 740c210d 1adce6ef 310d155b 07eb8110 07c540c4 891589e7 18259a83 a458ea53 a0ab60ca 32c7478e a052b1ed 9b3e8820 8967c0d2 1 1 987.0 null 2 105 2 1 2 2 1 1 2 68fd1e64 38d50e09 da603082 431a5096 43b19349 7e0ccccf 3f35b640 0b153874 a73ee510 3b08e48b 3d5fb018 6aaab577 94172618 07d13a8f ee569ce2 2f03ef40 d4bb7bd8 582152eb 21ddcdc9 b1252a9d 3b203ca1 32c7478e b21dc903 001f3601 aa5f0a15 1 null 47.0 null 0 6399 38 19 10 143 null 10 6 1464facd 38a947a1 223b0e16 ca55061c 25c83c98 7e0ccccf 6933dec1 5b392875 a73ee510 3b08e48b 860c302b 156f99ef 30735474 1adce6ef 0e78291e 5fbf4a84 e5ba7672 1999bae9 null null deb9605d 32c7478e e448275f null null 1 0 1.0 20 16 1548 93 42 32 912 0 15 16 8cf07265 942f9a8d a8e40bcf 0365276a 25c83c98 7e0ccccf 3f4ec687 1f89b562 a73ee510 726f00fd c4adf918 27c604a6 85dbe138 07d13a8f a8e962af c449f783 27c07bd6 1f868fdd 21ddcdc9 a458ea53 7eee76d1 32c7478e 9af06ad9 9d93af03 cdfe5ab7 1 0 20.0 2 2 7188 170 2 3 24 0 2 2 68fd1e64 38a947a1 ee6e4611 30d9fc77 4cf72387 7e0ccccf bf9d4f90 0b153874 a73ee510 b7c4dad5 81cae03e 5332e3fb d413ef3e 07d13a8f a6d97bf2 ec676ace 3486227d 02e8d897 null null b055c31b 3a171ecb ae2cd100 null null 1 0 78.0 2 15 4311 85 4 18 230 0 3 15 68fd1e64 1287a654 5ed035c9 5b5365b2 4cf72387 6f6d9be8 1b1aa9ea 0b153874 a73ee510 c3e69838 7a3651f5 df8b1dea 95bc260c b28479f6 ced5be3a 4cc0abe4 e5ba7672 df00d249 null null f520f961 32c7478e 27b60b01 null null 1 3 0.0 4 13 224 28 3 35 27 1 1 13 05db9164 90081f33 993f507e 14a74146 25c83c98 13718bbd dc7659bd 0b153874 a73ee510 03e48276 e51ddf94 18fe7085 3516f6e6 64c94865 98995c3b 8c48eb08 e5ba7672 7181ccc8 null null 2ed6b316 3a171ecb abf08f1b null null 1 null 277.0 null 3 7318 24 6 3 98 null 1 3 8cf07265 9adf4cf9 2e76fb61 0b1ad9da 4cf72387 fe6b92e5 75dcaaca 0b153874 a73ee510 3b08e48b 8aabdae8 9886a0a7 edcf17ce 07d13a8f 2aaebd23 338c0d09 e5ba7672 c7dbecd5 null null 60d2d691 3a171ecb 90b6276f null null 1 1 259.0 1 1 5 1 6 1 1 1 3 1 05db9164 f3b07830 ad981000 f96c819d 25c83c98 null df5c2d18 0b153874 a73ee510 8aef4905 a7b606c4 b912be9f eae197fd b28479f6 d27eed0e b8b09fe6 e5ba7672 048d01f4 null null 08ae854d 32c7478e c657e6e5 null null 1 0 127.0 1 3 1683 19 26 17 475 0 9 3 05db9164 8947f767 11c9d79e 52a787c8 4cf72387 fbad5c96 18671b18 0b153874 a73ee510 ceb10289 77212bd7 79507c6b 7203f04e 07d13a8f 2c14c412 49013ffe 8efede7f bd17c3da f6a3e43b a458ea53 35cd95c9 c7dc6720 3fdb382b 010f6491 49d68486 1 88 319.0 null 4 5 4 89 40 88 3 4 4 05db9164 08d6d899 333440d5 fc86bde0 25c83c98 fbad5c96 f00bddf8 0b153874 a73ee510 83ff688a 55795b33 1b0c8aa3 39795005 b28479f6 bffbd637 4a838997 8efede7f bbf70d82 null null 16e2e3b3 32c7478e d859b4dd null null 1 1 30.0 null 3 116 31 1 3 3 1 1 3 5a9ed9b0 38a947a1 0f90b6d6 16b922ed 25c83c98 fbad5c96 17b47bf9 0b153874 a73ee510 3b08e48b 76120d9d ee2d3fdb d4384424 07d13a8f 3046a70a 81371cbc d4bb7bd8 1bae7658 null null 37bad455 3a171ecb 9d96bacb null null 1 null 0.0 55 5 14477 null 0 5 1 null 0 5 05db9164 09e68b86 2beedeb2 c59396e7 25c83c98 7e0ccccf a972360e 0b153874 7cc72ec2 acf0058d 9e511730 8f70e33a 04e4a7e0 64c94865 91126f30 6df0eed9 e5ba7672 5aed7436 55dd3565 5840adea c412f773 3a171ecb 3fdb382b e8b83407 ccc71a58 1 null 1.0 7 3 10087 67 6 3 57 null 3 3 05db9164 d7988

In [62]:
# Testing the ReplaceNullWithMode custom transformer on column "c_1"
replaceNullWithModeTest = ReplaceNullWithValue(inputCol="c_1", outputCol="c_1", label = "label", value1 = mean_mode_clicked_d["c_1"] ,value2 = mean_mode_unclicked_d["c_1"] )
mode_pipeline = Pipeline(stages=[replaceNullWithModeTest])
mode_pipeline_model = mode_pipeline.fit(criteo_small_Parquet_DF)
data = mode_pipeline_model.transform(criteo_small_Parquet_DF)
display(data.select(["c_1"]))

c_1 68fd1e64 241546e0 be589b51 68fd1e64 1464facd 8cf07265 68fd1e64 68fd1e64 05db9164 8cf07265 05db9164 05db9164 05db9164 5a9ed9b0 05db9164 05db9164 05db9164 05db9164 05db9164 05db9164 05db9164 68fd1e64 5a9ed9b0 68fd1e64 05db9164 05db9164 5a9ed9b0 ae82ea21 05db9164 5a9ed9b0 be589b51 05db9164 68fd1e64 b455c6d7 68fd1e64 05db9164 05db9164 05db9164 05db9164 05db9164 8cf07265 8cf07265 87552397 68fd1e64 05db9164 68fd1e64 05db9164 05db9164 05db9164 5a9ed9b0 05db9164 05db9164 05db9164 68fd1e64 68fd1e64 05db9164 05db9164 87552397 5a9ed9b0 8cf07265 05db9164 68fd1e64 05db9164 68fd1e64 68fd1e64 05db9164 05db9164 68fd1e64 05db9164 05db9164 05db9164 8cf07265 05db9164 05db9164 45cb84c9 36a5b3ff 05db9164 5bfa8ab5 05db9164 05db9164 5a9ed9b0 5a9ed9b0 5a9ed9b0 8cf07265 05db9164 4a4e85c4 05db9164 68fd1e64 05db9164 05db9164 05db9164 05db9164 68fd1e64 8cf07265 8cf07265 05db9164 5a9ed9b0 5bfa8ab5 05db9164 241546e0 05db9164 05db9164 05db9164 05db9164 05db9164 b455c6d7 241546e0 5a9ed9b0 05db9164 05db9164 ae82ea21 05db9164 05db9164 05db9164 87552397 68fd1e64 8cf07265 5a9ed9b0 05db9164 05db9164 05db9164 5a9ed9b0 5a9ed9b0 05db9164 68fd1e64 24eda356 68fd1e64 05db9164 5bfa8ab5 05db9164 05db9164 05db9164 5bfa8ab5 5a9ed9b0 5a9ed9b0 5a9ed9b0 05db9164 05db9164 05db9164 05db9164 fb174e6b 8cf07265 05db9164 05db9164 09ca0b81 05db9164 05db9164 5bfa8ab5 05db9164 75ac2fe6 5a9ed9b0 05db9164 68fd1e64 05db9164 05db9164 05db9164 39af2607 68fd1e64 09ca0b81 17f69355 68fd1e64 68fd1e64 09ca0b81 68fd1e64 05db9164 8cf07265 68fd1e64 05db9164 05db9164 1a5f926e 05db9164 05db9164 05db9164 68fd1e64 05db9164 05db9164 05db9164 68fd1e64 87552397 05db9164 68fd1e64 8cf07265 05db9164 68fd1e64 05db9164 05db9164 68fd1e64 1a5f926e 05db9164 05db9164 dbe63c2b 05db9164 05db9164 05db9164 05db9164 05db9164 05db9164 8cf07265 05db9164 be589b51 05db9164 05db9164 64e77ae7 05db9164 68fd1e64 68fd1e64 68fd1e64 1464facd 05db9164 68fd1e64 05db9164 05db9164 05db9164 05db9164 5a9ed9b0 5a9ed9b0 05db9164 5a9ed9b0 05db9164 be589b51 68fd1e64 05db9164 8cf07265 68fd1e64 05db9164 05db9164 75ac2fe6 05db9164 05db9164 68fd1e64 68fd1e64 5a9ed9b0 68fd1e64 05db9164 05db9164 68fd1e64 05db9164 5bfa8ab5 8cf07265 05db9164 17f69355 05db9164 68fd1e64 5a9ed9b0 05db9164 05db9164 05db9164 68fd1e64 68fd1e64 05db9164 05db9164 05db9164 05db9164 05db9164 05db9164 05db9164 5a9ed9b0 05db9164 05db9164 05db9164 41edac3d 05db9164 05db9164 be589b51 be589b51 5a9ed9b0 5e53cc38 05db9164 68fd1e64 05db9164 05db9164 05db9164 68fd1e64 68fd1e64 05db9164 05db9164 5a9ed9b0 05db9164 05db9164 05db9164 68fd1e64 05db9164 05db9164 05db9164 5a9ed9b0 05db9164 5a9ed9b0 5a9ed9b0 be589b51 39af2607 68fd1e64 05db9164 05db9164 f473b8dc 8cf07265 68fd1e64 05db9164 05db9164 68fd1e64 05db9164 05db9164 be589b51 05db9164 68fd1e64 05db9164 8cf07265 05db9164 5a9ed9b0 68fd1e64 05db9164 05db9164 be589b51 68fd1e64 5bfa8ab5 68fd1e64 be589b51 05db9164 05db9164 05db9164 5a9ed9b0 8cf07265 68fd1e64 f473b8dc 05db9164 05db9164 05db9164 8cf07265 05db9164 05db9164 5a9ed9b0 05db9164 68fd1e64 8cf07265 05db9164 5bfa8ab5 5bfa8ab5 b455c6d7 8cf07265 05db9164 05db9164 05db9164 17f69355 05db9164 68fd1e64 8cf07265 5a9ed9b0 05db9164 05db9164 68fd1e64 05db9164 68fd1e64 05db9164 05db9164 05db9164 8cf07265 05db9164 05db9164 68fd1e64 05db9164 05db9164 8cf07265 f0a33555 05db9164 05db9164 8cf07265 9a89b36c 68fd1e64 68fd1e64 05db9164 87552397 05db9164 05db9164 05db9164 05db9164 287e684f 05db9164 05db9164 05db9164 05db9164 8cf07265 05db9164 68fd1e64 05db9164 05db9164 05db9164 d330a670 05db9164 d5b19c97 5a9ed9b0 05db9164 05db9164 be589b51 05db9164 68fd1e64 68fd1e64 87552397 68fd1e64 05db9164 05db9164 05db9164 05db9164 68fd1e64 05db9164 05db9164 8cf07265 05db9164 5a9ed9b0 68fd1e64 5a9ed9b0 8cf07265 05db9164 5a9ed9b0 05db9164 05db9164 68fd1e64 05db9164 05db9164 05db9164 8cf07265 9a89b36c 05db9164 41edac3d 5bfa8ab5 05db9164 8cf07265 05db9164 5bfa8ab5 5a9ed9b0 05db9164 68fd1e64 05db9164 05db9164 1464facd 05db9164 05db9164 68fd1e64 05db9164 05db9164 05db9164 8cf07265 05db9164 05db9164 75ac2fe6 5a9ed9b0 

### Replace outliers with the mean.


> <br>

In [64]:
# Find outliers in the data
# calculate the IQR and the upper and lower limit for each column
bounds = {
    c: dict(
        zip(["q1", "q3"], criteo_small_Parquet_DF.approxQuantile(c, [0.25, 0.75], 0))
    )
    for c in ["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
}

for c in bounds:
    iqr = bounds[c]['q3'] - bounds[c]['q1']
    bounds[c]['lower'] = bounds[c]['q1'] - (iqr * 1.5)
    bounds[c]['upper'] = bounds[c]['q3'] + (iqr * 1.5)
print(bounds)

{'i_2': {'q1': 0.0, 'q3': 39.0, 'lower': -58.5, 'upper': 97.5}, 'i_3': {'q1': 2.0, 'q3': 16.0, 'lower': -19.0, 'upper': 37.0}, 'i_4': {'q1': 2.0, 'q3': 9.0, 'lower': -8.5, 'upper': 19.5}, 'i_5': {'q1': 165.0, 'q3': 8596.0, 'lower': -12481.5, 'upper': 21242.5}, 'i_6': {'q1': 5.0, 'q3': 83.0, 'lower': -112.0, 'upper': 200.0}, 'i_7': {'q1': 1.0, 'q3': 14.0, 'lower': -18.5, 'upper': 33.5}, 'i_8': {'q1': 2.0, 'q3': 19.0, 'lower': -23.5, 'upper': 44.5}, 'i_9': {'q1': 10.0, 'q3': 112.0, 'lower': -143.0, 'upper': 265.0}, 'i_11': {'q1': 1.0, 'q3': 3.0, 'lower': -2.0, 'upper': 6.0}, 'i_13': {'q1': 1.0, 'q3': 9.0, 'lower': -11.0, 'upper': 21.0}}

In [65]:
# Finding the mean for the whole coulmn regardless of the label
from pyspark.sql.functions import col, avg, mean
ci=["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
mean_data=dict()
for i in ci:
  mean_data[i]=round(criteo_small_Parquet_DF.where(col(i).isNotNull()).select(mean(i)).first()[0] )

print(mean_data)

{'i_2': 116, 'i_3': 30, 'i_4': 7, 'i_5': 15435, 'i_6': 98, 'i_7': 19, 'i_8': 12, 'i_9': 108, 'i_11': 3, 'i_13': 7}

### Custom Transformer for Replacing Outliers with the Mean.


> <br>

In [67]:
# Adding a Transformer for replacing outliers with the mean
class ReplaceOutliersWithMean(Transformer, HasInputCol, HasOutputCol):
  
  @keyword_only
  def __init__(self, inputCol=None, outputCol=None, mean =None, upper = None, lower =None):
      super(ReplaceOutliersWithMean, self).__init__()
      self.mean = Param(self, "mean", "mean for the coulmn")
      self.upper = Param(self, "upper", "upper bound")
      self.lower = Param(self, "lower", "lower bound")
      kwargs = self._input_kwargs
      self.setParams(**kwargs)


  @keyword_only
  def setParams(self, inputCol=None, outputCol=None, mean =None, upper = None, lower =None):
      """Get params."""
      kwargs = self._input_kwargs
      return self._set(**kwargs)  
 
  def setMean(self, value):
      return self._set(mean=value)

  def getMean(self):
      return self.getOrDefault(self.mean)  
    
  def setUpper(self, value):
      return self._set(upper=value)

  def getUpper(self):
      return self.getOrDefault(self.upper)
  
  def setLower(self, value):
      return self._set(lower=value)

  def getLower(self):
      return self.getOrDefault(self.lower)  
    
  def _transform(self, dataframe):
      """Do transformation."""
      out_col = self.getOutputCol()
      in_col = dataframe[self.getInputCol()]
      return (dataframe
                .withColumn(out_col, (F.when( (in_col > self.getUpper())  | (in_col < self.getLower()), self.getMean())
                                      .otherwise(in_col))))

In [68]:
# Testing the ReplaceOutliersWithMean custom transformer on column "i_3"

replaceOutlierWithMeanTest = ReplaceOutliersWithMean(inputCol="i_3", outputCol= "i_3_capped", mean= mean_data["i_3"] , upper = bounds["i_3"]["upper"] , lower = bounds["i_3"]["lower"])
outlier_pipeline = Pipeline(stages=[replaceOutlierWithMeanTest])
outlier_pipeline_model = outlier_pipeline.fit(criteo_small_Parquet_DF)
data = outlier_pipeline_model.transform(criteo_small_Parquet_DF)
display(data.select(["i_3","i_3_capped"]))

i_3 i_3_capped 5 5 44 27 1 1 null null null null null null 2 2 2 2 4 4 null null 632 27 6 6 null null 11 11 84 27 1 1 null null null null 4 4 null null null null 80 27 14 14 9 9 2 2 16 16 20 20 2 2 2 2 4 4 null null null null 1 1 55 27 1 1 1 1 null null null null 3 3 15 15 2 2 null null 18 18 null null null null null null 6 6 2 2 13 13 null null 8 8 null null 2 2 22 22 16 16 28 28 9 9 12 12 2 2 20 20 2 2 5 5 42 42 55 27 5 5 7 7 40 40 10 10 null null 15 15 4 4 89 27 2 2 1 1 null null 11 11 2 2 null null 60 27 2 2 null null null null 80 27 91 27 null null null null 10 10 1 1 1 1 75 27 2 2 null null null null 64 27 1 1 1 1 90 27 78 27 null null 3 3 null null 5 5 null null 2 2 6 6 3 3 12 12 0 0 30 30 null null 3 3 null null 5 5 null null 16 16 null null 73 27 null null 5 5 2 2 44 27 31 31 23 23 14 14 null null null null 35 35 null null 1 1 null null 1 1 9 9 1 1 4 4 5 5 17 17 10 10 5 5 113 27 1 1 24 24 1 1 null null null null 1 1 2 2 7 7 14 14 null null 2 2 1 1 4 4 null null null null 21 21 null null 12 12 4 4 8 8 1 1 1 1 2 2 null null 10 10 182 27 null null 11 11 157 27 null null 1 1 2 2 13 13 3 3 2 2 2 2 15 15 null null 5 5 3 3 null null 6 6 6 6 7 7 4 4 1 1 null null null null null null 3 3 26 26 4 4 7 7 null null null null 2 2 153 27 4 4 8 8 5 5 32 32 23 23 106 27 null null 1 1 3 3 7 7 3 3 null null 3 3 0 0 2 2 null null 33 33 4 4 1 1 5 5 2 2 1 1 5 5 28 28 6 6 null null 5 5 null null 6 6 10 10 24 24 null null 12 12 4 4 null null null null 34 34 null null null null 51 27 2 2 3 3 null null 62 27 null null 1 1 null null null null 2 2 1 1 3 3 4 4 null null 27 27 null null 3 3 31 31 6 6 31 31 null null 128 27 null null 1 1 null null 7 7 1 1 3 3 13 13 2 2 1 1 null null 35 35 13 13 null null 1 1 51 27 null null 3 3 8 8 56 27 1 1 null null 181 27 29 29 1 1 0 0 null null 2 2 null null null null 6 6 1 1 null null 3 3 null null 2 2 21 21 3 3 5 5 6 6 33 33 7 7 null null 32 32 2 2 1 1 1 1 22 22 null null 5 5 6 6 2 2 8 8 29 29 null null 5 5 1 1 null null 20 20 null null 3 3 114 27 42 42 1 1 18 18 null null 17 17 null null 2 2 24 24 2 2 null null 27 27 83 27 2 2 2 2 null null 2 2 1 1 null null 2 2 3 3 2 2 110 27 1 1 3 3 67 27 8 8 null null 3 3 3 3 23 23 null null 4 4 2 2 null null 2 2 1 1 1 1 4 4 null null 4 4 75 27 1 1 null null 15 15 47 27 11 11 3 3 1 1 3 3 null null 1 1 16 16 null null 2 2 89 27 3 3 null null 7 7 null null 4 4 8 8 1 1 92 27 null null 3 3 9 9 1 1 1361 27 null null 5 5 5 5 7 7 null null null null 1 1 12 12 2 2 13 13 null null 1 1 2 2 null null 1 1 null null null null 7 7 6 6 null null null null 11 11 15 15 44 27 5 5 4 4 null null 2 2 12 12 6 6 15 15 null null 9 9 1 1 null null 2 2 2 2 null null 12 12 4 4 null null 1 1 null null 1 1 14 14 2 2 2 2 21 21 null null 19 19 null null 6 6 1 1 8 8 8 8 7 7 5 5 64 27 28 28 161 27 0 0 null null 4 4 0 0 18 18 5 5 10 10 3 3 null null null null 2 2 null null 4 4 27 27 74 27 13 13 1 1 22 22 3 3 6 6 3 3 4 4 1 1 10 10 null null 12 12 20 20 4 4 2 2 1 1 2 2 null null 1 1 1 1 23 23 13 13 5 5 21 21 7 7 10 10 6 6 11 11 9 9 15 15 4 4 null null 6 6 11 11 14 14 null null 1372 27 null null 1371 27 6 6 6 6 1 1 null null 25 25 37 37 9 9 3 3 1 1 200 27 null null 4 4 14 14 20 20 39 39 8 8 14 14 2 2 null null 1 1 100 27 10 10 1 1 2 2 null null 90 27 47 27 7 7 33 33 4 4 null null null null 153 27 3 3 37 37 490 27 7 7 3 3 null null 10 10 2 2 null null null null 12 12 17 17 9 9 30 30 null null 1 1 1 1 null null 3 3 5 5 15 15 9 9 2 2 47 27 1 1 4 4 8 8 null null 5 5 19 19 8 8 null null 3 3 6 6 null null 1 1 1 1 784 27 5 5 2 2 4 4 null null 35 35 3 3 null null 20 20 3 3 2 2 2 2 2 2 45 27 21 21 4 4 44 27 25 25 2 2 2 2 6 6 null null 63 27 33 33 5 5 64 27 8 8 null null null null 17 17 1 1 76 27 11 11 5 5 78 27 1 1 7 7 null null 1 1 6 6 1 1 null null 11 11 2 2 11 11 1 1 4 4 null null 3 3 14 14 10 10 37 37 2 2 1 1 1 1 null null 5 5 36 36 19 19 11 11 3 3 9 9 12 12 6 6 1 1 33 33 6 6 84 27 115 27 7 7 5 5 8 8 9 9 5 5 133 27 null null null null 17 17 13 13 5 5 null null null null 8 8 3 3 364 27 1 1 74 27 32 32 128 27 1 1 n

In [69]:
# Replacing the outliers with the mean 
from pyspark.sql.functions import col, expr, when
from pyspark.sql import functions as F
for cl in ["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]:
  replaceOutlierWithMean = ReplaceOutliersWithMean(inputCol=cl, outputCol=cl, mean=mean_data[cl] , upper =bounds[cl]['upper'] , lower = bounds[cl]['lower'])
  stages += [replaceOutlierWithMean]


### Counting Distinct Values in Categorical Columns


> <br>

In [71]:
# Count the distinct values for the categorical coulmns c_1 to c_26 excluding the c22 because we dropped it
columns=["c_1","c_2","c_3","c_4","c_5","c_6","c_7","c_8","c_9","c_10","c_11","c_12","c_13","c_14","c_15","c_16","c_17","c_18","c_21","c_23","c_24"]
critieo_cat_distinct=dict()
for col in columns:
  critieo_cat_distinct[col]=criteo_small_Parquet_DF.select(col).distinct().count()
  
print(critieo_cat_distinct)  

{'c_1': 1460, 'c_2': 572, 'c_3': 5736859, 'c_4': 1371678, 'c_5': 305, 'c_6': 24, 'c_7': 12413, 'c_8': 633, 'c_9': 3, 'c_10': 79045, 'c_11': 5555, 'c_12': 4839595, 'c_13': 3190, 'c_14': 27, 'c_15': 14126, 'c_16': 3256816, 'c_17': 10, 'c_18': 5388, 'c_21': 4117056, 'c_23': 15, 'c_24': 202140}

In [72]:
# Sort the dictionary
# Count the distinct values for the categorical coulmns c_1 to c_26 excluding the c22
sort_critieo_cat_distinct = sorted(critieo_cat_distinct.items(), key=lambda x: x[1], reverse=True)
for item in sort_critieo_cat_distinct:
  print(item)

('c_3', 5736859)
('c_12', 4839595)
('c_21', 4117056)
('c_16', 3256816)
('c_4', 1371678)
('c_24', 202140)
('c_10', 79045)
('c_15', 14126)
('c_7', 12413)
('c_11', 5555)
('c_18', 5388)
('c_13', 3190)
('c_1', 1460)
('c_8', 633)
('c_2', 572)
('c_5', 305)
('c_14', 27)
('c_6', 24)
('c_23', 15)
('c_17', 10)
('c_9', 3)

### Transform the categorical values (strings) into indexes


> <br>

In [74]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer

In [75]:
# Used stringIndexer() on categorical columns (high cardinality)
cat_Col_H = ["c_1","c_2","c_3","c_4","c_5","c_7","c_8","c_10","c_11","c_12","c_13","c_15","c_16","c_18","c_21","c_24"]
indexers = [StringIndexer(inputCol=column, outputCol=column+"_indexH").fit(criteo_small_Parquet_DF) for column in cat_Col_H ]


stages += indexers



In [76]:
# Used stringIndexer() on categorical columns (low cardinality)
cat_Col_L = ["c_6","c_9","c_14","c_17","c_23"]
indexers = [StringIndexer(inputCol=column, outputCol=column+"_indexL").fit(criteo_small_Parquet_DF) for column in cat_Col_L ]
stages += indexers


In [77]:
print(criteo_small_Parquet_DF.columns)

['label', 'i_1', 'i_2', 'i_3', 'i_4', 'i_5', 'i_6', 'i_7', 'i_8', 'i_9', 'i_10', 'i_11', 'i_13', 'c_19', 'c_20', 'c_25', 'c_26', 'c_1_indexH', 'c_2_indexH', 'c_3_indexH', 'c_4_indexH', 'c_5_indexH', 'c_7_indexH', 'c_8_indexH', 'c_10_indexH', 'c_11_indexH', 'c_12_indexH', 'c_13_indexH', 'c_15_indexH', 'c_16_indexH', 'c_18_indexH', 'c_21_indexH', 'c_24_indexH', 'c_6_indexL', 'c_9_indexL', 'c_14_indexL', 'c_17_indexL', 'c_23_indexL']

In [78]:
criteo_small_Parquet_DF.rdd.take(1)

Out[16]: [Row(label=0, i_1=False, i_2=6.0, i_3=5.0, i_4=7.600443351827682, i_5=15504.0, i_6=137.16348976964676, i_7=13.06159185728511, i_8=5.0, i_9=103.65096289863389, i_10=False, i_11=2.2526029754460692, i_13=8.961150238166741, c_19=True, c_20=True, c_25=True, c_26=True, c_1_indexH=0.0, c_2_indexH=24.0, c_3_indexH=57239.0, c_4_indexH=1160.0, c_5_indexH=0.0, c_7_indexH=450.0, c_8_indexH=0.0, c_10_indexH=900.0, c_11_indexH=236.0, c_12_indexH=56707.0, c_13_indexH=241.0, c_15_indexH=9.0, c_16_indexH=3648.0, c_18_indexH=17.0, c_21_indexH=5196.0, c_24_indexH=589.0, c_6_indexL=0.0, c_9_indexL=0.0, c_14_indexL=1.0, c_17_indexL=0.0, c_23_indexL=0.0)]

In [79]:
# checking the mleap version
import mleap
print (mleap.__version__)

0.16.1

### Z Scoring The Values of the Integer Columns


> <br>

### Custom Transformer for Z Scoring The Values of the Integer Columns


> <br>

In [82]:
from pyspark.sql.functions import col, stddev_samp,stddev,mean

class ZScoring(Transformer, HasInputCol, HasOutputCol):
  
  @keyword_only
  def __init__(self, inputCol=None, outputCol=None):
      super(ZScoring, self).__init__()
      kwargs = self._input_kwargs
      self.setParams(**kwargs)
   
  @keyword_only
  def setParams(self, inputCol=None, outputCol=None):
      """Get params."""
      kwargs = self._input_kwargs
      return self._set(**kwargs)  
    
  
  def _transform(self, dataframe):
      """Do transformation."""
      out_col = self.getOutputCol()
      in_col = dataframe[self.getInputCol()]
      col_mean = dataframe.select(mean(in_col)).first()[0]
      stdv= dataframe.agg(stddev(in_col)).first()[0]
      return (dataframe.withColumn(out_col, (in_col - col_mean) / stdv))

In [83]:
# Testing the zscoring custom transformer on column "i_2"
ZScoringTest = ZScoring(inputCol="i_2", outputCol="i_2_scaled" )
ZScoringTest_pipeline = Pipeline(stages=[ZScoringTest])
ZScoringTest_pipeline_model = ZScoringTest_pipeline.fit(criteo_small_Parquet_DF)
data = ZScoringTest_pipeline_model.transform(criteo_small_Parquet_DF)
display(data.select(["i_2","i_2_scaled"]))

i_2 i_2_scaled 1 -0.2678409108750413 0 -0.2703954645000928 0 -0.2703954645000928 893 2.010820922670842 -1 -0.2729500181251442 -1 -0.2729500181251442 1 -0.2678409108750413 4 -0.260177249999887 44 -0.15799510499782946 35 -0.1809860876232924 2 -0.2652863572499899 6 -0.2550681427497841 -1 -0.2729500181251442 2 -0.2652863572499899 51 -0.1401132296224694 2 -0.2652863572499899 987 2.250948963425677 1 -0.2678409108750413 24 -0.20908617749885822 102 -0.009830994744846017 47 -0.15033144412267513 1 -0.2678409108750413 0 -0.2703954645000928 9 -0.2474044818746298 1 -0.2678409108750413 4 -0.260177249999887 1 -0.2678409108750413 20 -0.21930439199906399 78 -0.07114028174608054 0 -0.2703954645000928 277 0.43721588963915575 -1 -0.2729500181251442 0 -0.2703954645000928 0 -0.2703954645000928 259 0.39123392438822985 127 0.054032845881439945 1 -0.2678409108750413 -1 -0.2729500181251442 0 -0.2703954645000928 0 -0.2703954645000928 38 -0.17332242674813808 319 0.5445071418913161 1 -0.2678409108750413 27 -0.20142251662370392 -1 -0.2729500181251442 32 -0.1886497484984467 6 -0.2550681427497841 17 -0.22696805287421828 2382 5.8145512703724345 190 0.21496972425968058 19 -0.22185894562411543 30 -0.1937588557485496 6 -0.2550681427497841 2 -0.2652863572499899 55 -0.12989501512226362 0 -0.2703954645000928 19 -0.22185894562411543 18 -0.22441349924916687 1 -0.2678409108750413 0 -0.2703954645000928 56 -0.1273404614972122 76 -0.07624938899618341 8 -0.24995903549968124 0 -0.2703954645000928 1 -0.2678409108750413 1 -0.2678409108750413 1 -0.2678409108750413 0 -0.2703954645000928 51 -0.1401132296224694 0 -0.2703954645000928 1 -0.2678409108750413 0 -0.2703954645000928 39 -0.17076787312308664 2 -0.2652863572499899 -1 -0.2729500181251442 0 -0.2703954645000928 140 0.08724204300710865 0 -0.2703954645000928 1 -0.2678409108750413 34 -0.18354064124834385 0 -0.2703954645000928 1 -0.2678409108750413 13 -0.23718626737442405 0 -0.2703954645000928 -1 -0.2729500181251442 53 -0.1350041223723665 -1 -0.2729500181251442 0 -0.2703954645000928 23 -0.21164073112390966 1 -0.2678409108750413 127 0.054032845881439945 -1 -0.2729500181251442 -1 -0.2729500181251442 1 -0.2678409108750413 1 -0.2678409108750413 105 -0.0021673338696917015 35 -0.1809860876232924 0 -0.2703954645000928 1715 4.110664002463125 48 -0.14777689049762371 -1 -0.2729500181251442 1759 4.223064361965387 61 -0.11456769337195499 30 -0.1937588557485496 0 -0.2703954645000928 22 -0.2141952847489611 22 -0.2141952847489611 -1 -0.2729500181251442 5 -0.25762269637483554 1 -0.2678409108750413 0 -0.2703954645000928 14 -0.2346317137493726 2 -0.2652863572499899 207 0.258397135885555 7 -0.2525135891247327 17 -0.22696805287421828 6 -0.2550681427497841 -1 -0.2729500181251442 1 -0.2678409108750413 3 -0.2627318036249384 16 -0.22952260649926973 0 -0.2703954645000928 37 -0.17587698037318952 156 0.12811490100793166 -1 -0.2729500181251442 68 -0.09668581799659492 11 -0.24229537462452694 0 -0.2703954645000928 2903 7.145473709024234 -1 -0.2729500181251442 2 -0.2652863572499899 0 -0.2703954645000928 2537 6.210507082255407 -1 -0.2729500181251442 1 -0.2678409108750413 0 -0.2703954645000928 1261 2.950896656689771 -1 -0.2729500181251442 0 -0.2703954645000928 7 -0.2525135891247327 31 -0.19120430212349815 59 -0.11967680062205788 54 -0.13244956874731506 2568 6.289698244632001 0 -0.2703954645000928 5 -0.25762269637483554 27 -0.20142251662370392 1 -0.2678409108750413 -1 -0.2729500181251442 6 -0.2550681427497841 1 -0.2678409108750413 179 0.18686963438411475 -1 -0.2729500181251442 -1 -0.2729500181251442 -1 -0.2729500181251442 328 0.5674981245167791 1392 3.28554318157151 1249 2.920242013189154 8 -0.24995903549968124 1 -0.2678409108750413 26 -0.20397707024875536 1 -0.2678409108750413 1 -0.2678409108750413 125 0.04892373863133707 46 -0.15288599774772657 -1 -0.2729500181251442 0 -0.2703954645000928 7 -0.2525135891247327 355 0.6364710723931679 0 -0.2703954645000928 -1 -0.2729500181251442 -1 -0.2729500181251442 0 -0.2703954645000928 2 -0.2652863572499899 0 -0.270395464500

In [84]:
# z-scoring (scalling) the integer coulmns "i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"
from pyspark.sql.functions import col, stddev_samp,stddev
col_to_scale=["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
for cl in col_to_scale:
  zSoring = ZScoring(inputCol=cl, outputCol=cl+"_scaled")
  stages += [zSoring]
  

In [85]:
print(criteo_small_Parquet_DF.columns)

['label', 'i_1', 'i_2', 'i_3', 'i_4', 'i_5', 'i_6', 'i_7', 'i_8', 'i_9', 'i_10', 'i_11', 'i_13', 'c_1', 'c_2', 'c_3', 'c_4', 'c_5', 'c_6', 'c_7', 'c_8', 'c_9', 'c_10', 'c_11', 'c_12', 'c_13', 'c_14', 'c_15', 'c_16', 'c_17', 'c_18', 'c_19', 'c_20', 'c_21', 'c_23', 'c_24', 'c_25', 'c_26']

In [86]:
criteo_small_Parquet_DF.rdd.take(1)

Out[34]: [Row(label=1, i_1=1, i_2=4, i_3=2, i_4=0, i_5=0, i_6=0, i_7=1, i_8=0, i_9=0, i_10=1, i_11=1, i_13=0, c_1='68fd1e64', c_2='2c16a946', c_3='503b9dbc', c_4='e4dbea90', c_5='f3474129', c_6='13718bbd', c_7='38eb9cf4', c_8='1f89b562', c_9='a73ee510', c_10='547c0ffe', c_11='bc8c9f21', c_12='60ab2f07', c_13='46f42a63', c_14='07d13a8f', c_15='18231224', c_16='e6b6bdc7', c_17='e5ba7672', c_18='74ef3502', c_19=None, c_20=None, c_21='5316a17f', c_23='32c7478e', c_24='9117a34a', c_25=None, c_26=None)]

### Binning The Values of the Integer Columns


> <br>

In [88]:
# Binning( bucketizing the values)
from pyspark.ml.feature import Bucketizer
col_to_bin=["i_2","i_3","i_4","i_5","i_6","i_7","i_8","i_9","i_11","i_13"]
splits = [-float('inf'), -.5, 0.0, .5, float('inf')]
for cl in col_to_bin:
  bucketizer=Bucketizer(splits=splits,inputCol=cl+"_scaled",outputCol=cl+"_bucket")
  stages += [bucketizer]
  

In [89]:
criteo_small_Parquet_DF.rdd.take(1)

Out[36]: [Row(label=1, i_1=1, i_2=4, i_3=2, i_4=0, i_5=0, i_6=0, i_7=1, i_8=0, i_9=0, i_10=1, i_11=1, i_13=0, c_1='68fd1e64', c_2='2c16a946', c_3='503b9dbc', c_4='e4dbea90', c_5='f3474129', c_6='13718bbd', c_7='38eb9cf4', c_8='1f89b562', c_9='a73ee510', c_10='547c0ffe', c_11='bc8c9f21', c_12='60ab2f07', c_13='46f42a63', c_14='07d13a8f', c_15='18231224', c_16='e6b6bdc7', c_17='e5ba7672', c_18='74ef3502', c_19=None, c_20=None, c_21='5316a17f', c_23='32c7478e', c_24='9117a34a', c_25=None, c_26=None)]

### One Hot Code Encoding The Low Dimensional Categorical Columns (low cardinality)


> <br>

In [91]:
# One hot encoding only the low dimentional categorical values
from pyspark.ml.feature import OneHotEncoder

for cl in ["c_6_indexL","c_9_indexL","c_14_indexL","c_17_indexL","c_23_indexL"]:
  
  OHE = (OneHotEncoder()
                .setInputCol(cl)
                .setOutputCol(cl[:cl.index("_index")]+"_OHE"))

  stages += [OHE]


In [92]:
from pyspark.sql.functions import col
criteo_small_Parquet_DF.filter(col('label')==1).count()

Out[96]: 11745438

### Select The Relevant Columns To Use for Assembling Into a Vector


> <br>

In [94]:
print(criteo_small_Parquet_DF.columns)

['label', 'i_1', 'i_2', 'i_3', 'i_4', 'i_5', 'i_6', 'i_7', 'i_8', 'i_9', 'i_10', 'i_11', 'i_13', 'c_1', 'c_2', 'c_3', 'c_4', 'c_5', 'c_6', 'c_7', 'c_8', 'c_9', 'c_10', 'c_11', 'c_12', 'c_13', 'c_14', 'c_15', 'c_16', 'c_17', 'c_18', 'c_19', 'c_20', 'c_21', 'c_23', 'c_24', 'c_25', 'c_26']

In [95]:
# Select The Relevant Columns To Use for Assembling Into a Vector
catgoricalLowDimention = ["c_6_OHE","c_9_OHE","c_14_OHE","c_17_OHE","c_23_OHE"]
catgoricalHighDimention = ["c_1_indexH","c_2_indexH","c_3_indexH","c_4_indexH","c_5_indexH","c_7_indexH","c_8_indexH","c_10_indexH","c_11_indexH","c_12_indexH","c_13_indexH","c_15_indexH","c_16_indexH","c_18_indexH","c_21_indexH","c_24_indexH"]
booleanCoulmns = ['i_1', 'i_10', 'c_19', 'c_20', 'c_25', 'c_26']
bucketizedCoulmns = ["i_2_bucket","i_3_bucket","i_4_bucket","i_5_bucket","i_6_bucket","i_7_bucket","i_8_bucket","i_9_bucket","i_11_bucket","i_13_bucket"]

relevantCols = bucketizedCoulmns + booleanCoulmns + catgoricalHighDimention + catgoricalLowDimention

### Vector assembler the Relevant Columns into Features column


> <br>

In [97]:
# Let us import the vector assembler
from pyspark.ml.feature import VectorAssembler
assembler = VectorAssembler(inputCols=relevantCols,outputCol="features")
stages += [assembler]


### Running The Vector Assembler Pipeline


> <br>

In [99]:
# Create a Pipeline and fit & transform the pipline to the dataset.
from pyspark.ml import Pipeline


pipeline = Pipeline(stages = stages)
pipelineModel = pipeline.fit(criteo_small_Parquet_DF)
criteo_small_Parquet_DF = pipelineModel.transform(criteo_small_Parquet_DF)


In [100]:
print(criteo_small_Parquet_DF.columns)

['label', 'i_1', 'i_2', 'i_3', 'i_4', 'i_5', 'i_6', 'i_7', 'i_8', 'i_9', 'i_10', 'i_11', 'i_13', 'c_1', 'c_2', 'c_3', 'c_4', 'c_5', 'c_6', 'c_7', 'c_8', 'c_9', 'c_10', 'c_11', 'c_12', 'c_13', 'c_14', 'c_15', 'c_16', 'c_17', 'c_18', 'c_19', 'c_20', 'c_21', 'c_23', 'c_24', 'c_25', 'c_26', 'c_1_indexH', 'c_2_indexH', 'c_3_indexH', 'c_4_indexH', 'c_5_indexH', 'c_7_indexH', 'c_8_indexH', 'c_10_indexH', 'c_11_indexH', 'c_12_indexH', 'c_13_indexH', 'c_15_indexH', 'c_16_indexH', 'c_18_indexH', 'c_21_indexH', 'c_24_indexH', 'c_6_indexL', 'c_9_indexL', 'c_14_indexL', 'c_17_indexL', 'c_23_indexL', 'i_2_scaled', 'i_3_scaled', 'i_4_scaled', 'i_5_scaled', 'i_6_scaled', 'i_7_scaled', 'i_8_scaled', 'i_9_scaled', 'i_11_scaled', 'i_13_scaled', 'i_2_bucket', 'i_3_bucket', 'i_4_bucket', 'i_5_bucket', 'i_6_bucket', 'i_7_bucket', 'i_8_bucket', 'i_9_bucket', 'i_11_bucket', 'i_13_bucket', 'c_6_OHE', 'c_9_OHE', 'c_14_OHE', 'c_17_OHE', 'c_23_OHE', 'features']

In [101]:
criteo_small_Parquet_DF.rdd.take(1)

Out[43]: [Row(label=1, i_1=True, i_2=4.0, i_3=2.0, i_4=0.0, i_5=0.0, i_6=0.0, i_7=1.0, i_8=0.0, i_9=0.0, i_10=True, i_11=1.0, i_13=0.0, c_1='68fd1e64', c_2='2c16a946', c_3='503b9dbc', c_4='e4dbea90', c_5='f3474129', c_6='13718bbd', c_7='38eb9cf4', c_8='1f89b562', c_9='a73ee510', c_10='547c0ffe', c_11='bc8c9f21', c_12='60ab2f07', c_13='46f42a63', c_14='07d13a8f', c_15='18231224', c_16='e6b6bdc7', c_17='e5ba7672', c_18='74ef3502', c_19=False, c_20=False, c_21='5316a17f', c_23='32c7478e', c_24='9117a34a', c_25=False, c_26=False, c_1_indexH=1.0, c_2_indexH=14.0, c_3_indexH=1795394.0, c_4_indexH=65.0, c_5_indexH=9.0, c_7_indexH=10.0, c_8_indexH=2.0, c_10_indexH=24.0, c_11_indexH=251.0, c_12_indexH=1512608.0, c_13_indexH=2.0, c_15_indexH=22.0, c_16_indexH=3013320.0, c_18_indexH=33.0, c_21_indexH=4032151.0, c_24_indexH=6.0, c_6_indexL=4.0, c_9_indexL=0.0, c_14_indexL=0.0, c_17_indexL=0.0, c_23_indexL=0.0, i_2_scaled=-0.5625339611545624, i_3_scaled=-1.0095130180763698, i_4_scaled=-1.4026114831930216, i_5_scaled=-0.8712937899062695, i_6_scaled=-1.0959530799796187, i_7_scaled=-0.8461621782680571, i_8_scaled=-0.9758134202157372, i_9_scaled=-1.0269321356322059, i_11_scaled=-0.5590723668557998, i_13_scaled=-1.2993983763787638, i_2_bucket=0.0, i_3_bucket=0.0, i_4_bucket=0.0, i_5_bucket=0.0, i_6_bucket=0.0, i_7_bucket=0.0, i_8_bucket=0.0, i_9_bucket=0.0, i_11_bucket=0.0, i_13_bucket=0.0, c_6_OHE=SparseVector(22, {4: 1.0}), c_9_OHE=SparseVector(2, {0: 1.0}), c_14_OHE=SparseVector(26, {0: 1.0}), c_17_OHE=SparseVector(9, {0: 1.0}), c_23_OHE=SparseVector(14, {0: 1.0}), features=SparseVector(105, {10: 1.0, 11: 1.0, 16: 1.0, 17: 14.0, 18: 1795394.0, 19: 65.0, 20: 9.0, 21: 10.0, 22: 2.0, 23: 24.0, 24: 251.0, 25: 1512608.0, 26: 2.0, 27: 22.0, 28: 3013320.0, 29: 33.0, 30: 4032151.0, 31: 6.0, 36: 1.0, 54: 1.0, 56: 1.0, 82: 1.0, 91: 1.0}))]

In [102]:
dataset = criteo_small_Parquet_DF.select(["label","features"])
dataset.rdd.take(1)

Out[44]: [Row(label=1, features=SparseVector(105, {10: 1.0, 11: 1.0, 16: 1.0, 17: 14.0, 18: 1795394.0, 19: 65.0, 20: 9.0, 21: 10.0, 22: 2.0, 23: 24.0, 24: 251.0, 25: 1512608.0, 26: 2.0, 27: 22.0, 28: 3013320.0, 29: 33.0, 30: 4032151.0, 31: 6.0, 36: 1.0, 54: 1.0, 56: 1.0, 82: 1.0, 91: 1.0}))]

### Split The Data into Training and Testing Set


> <br>

In [104]:
# Splitting the data into training and testing sets
criteoTest, criteoTrain = criteo_small_Parquet_DF.randomSplit([.25, .75], seed=0)

# Cache as we'll be using these several times
criteoTest.cache()
criteoTrain.cache()

print('Items in test datset: {0}'.format(criteoTest.count()))
print('Items in train dataset: {0}'.format(criteoTrain.count()))

Items in test datset: 5871506
Items in train dataset: 17619603

In [105]:
# Cast the features coulmn data type to String type to be easily handeled in python (producer/consumer)
from pyspark.sql.functions import col

criteoTest=criteoTest.withColumn("features1",col("features").cast(StringType()))



In [106]:
print(criteoTest.filter(col('label')==1).count())
print(criteoTest.filter(col('label')==0).count())
print(criteoTrain.filter(col('label')==1).count())
print(criteoTrain.filter(col('label')==0).count())


2935787
2935719
8809651
8809952

### Save The Training and Testing Set


> <br>

In [108]:
# Save the train data
criteoTrainParquet = "/tmp/criteosmall_train.parquet"

(criteoTrain.write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "snappy")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoTrainParquet)               # Write DataFrame to parquet files
)



criteoTestParquet = "/FileStore/test/criteosmall_test.parquet"

(criteoTest.coalesce(1).write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "gzip")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoTestParquet)               # Write DataFrame to parquet files
)

In [109]:
# Save the test data
criteoTestParquet = "/FileStore/test/criteosmall_test_uncompressed.parquet"

(criteoTest.coalesce(1).write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "uncompressed")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoTestParquet)               # Write DataFrame to parquet files
)

In [110]:
newTestData=criteoTest["label","features1"]
display(newTestData)

label features1 0 (110,[12,15,16,17,18,19,20,21,22,23,24,27,29,30,31,32,33,34,35,36,37,59,62,89,96],[5.0,954.0,4.0,1.0,5.0,1.0,1401.0,1.0,2.0,450.0,1.0,3.0,1.0,3.0,3.0,3.0,2.0,3.0,2.0,1.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,15,16,17,18,20,21,23,24,27,28,30,31,34,37,59,61,87,96],[5.0,1.0,1476.0,4.0,1.0,5.0,588.0,1.0,82.0,1.0,2.0,3.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,15,16,17,18,20,21,23,24,29,30,31,33,34,36,37,59,61,87,96],[5.0,2.0,141.0,4.0,1.0,5.0,6273.0,1.0,1486.0,1.0,3.0,1.0,2.0,3.0,1.0,2.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,15,16,17,18,19,20,21,23,24,27,29,31,36,37,59,63,87,96],[6.0,65.0,5.0,1.0,8.0,2.0,977.0,1.0,687.0,1.0,1.0,1.0,3.0,1.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,15,16,17,18,20,21,23,24,27,28,29,30,32,34,35,36,37,59,61,87,96],[6.0,13.0,238.0,5.0,1.0,8.0,335.0,1.0,82.0,1.0,3.0,3.0,3.0,1.0,2.0,1.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,15,16,17,18,20,21,23,24,25,30,31,34,37,59,61,87,98],[9.0,108.0,17.0,1.0,16.0,1305.0,1.0,173.0,1.0,2.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,15,16,17,18,20,21,22,23,24,28,29,31,36,37,59,61,94,96],[10.0,1.0,13.0,3.0,1.0,2.0,588.0,1.0,7.0,82.0,1.0,3.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,15,16,17,18,19,20,21,22,23,24,30,31,32,33,34,35,37,59,62,92,96],[13.0,1026.0,7.0,1.0,4.0,1.0,5268.0,1.0,5.0,1097.0,1.0,1.0,1.0,3.0,1.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,20,21,22,23,24,28,29,30,31,32,33,34,35,36,37,60,61,95,96],[14.0,1.0,29.0,1.0,10.0,3820.0,1.0,8.0,2056.0,1.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,20,21,22,23,24,28,29,30,31,32,34,35,36,37,60,61,95,96],[14.0,1.0,29.0,1.0,10.0,4868.0,1.0,8.0,1921.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,28,29,30,31,32,34,35,36,37,60,62,95,96],[14.0,1.0,29.0,1.0,10.0,1.0,1057.0,1.0,8.0,735.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,25,30,31,37,60,62,95,99],[14.0,1.0,29.0,1.0,10.0,1.0,1057.0,1.0,8.0,735.0,1.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,25,28,29,30,31,32,34,35,36,37,60,62,95,97],[14.0,1.0,29.0,1.0,10.0,1.0,1447.0,1.0,8.0,940.0,1.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,28,29,30,31,32,34,35,36,37,60,62,95,96],[14.0,1.0,29.0,1.0,10.0,1.0,1584.0,1.0,8.0,261.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,27,28,29,30,31,32,34,35,36,37,60,62,95,96],[14.0,1.0,29.0,1.0,10.0,1.0,1584.0,1.0,8.0,261.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,25,28,29,30,31,32,34,35,36,37,60,62,95,99],[14.0,1.0,29.0,1.0,10.0,1.0,2863.0,1.0,8.0,446.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,29,30,31,34,36,37,60,62,95,96],[14.0,1.0,29.0,1.0,10.0,1.0,2945.0,1.0,8.0,1244.0,1.0,3.0,3.0,3.0,1.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,14,16,17,18,19,20,21,22,23,24,25,27,28,30,31,37,60,63,95,98],[14.0,1.0,29.0,1.0,10.0,2.0,1663.0,1.0,8.0,403.0,1.0,2.0,1.0,2.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,14,16,17,18,19,20,21,22,23,24,28,29,30,31,36,37,60,62,95,96],[14.0,1.0,1.0,29.0,1.0,10.0,1.0,1057.0,1.0,8.0,735.0,1.0,3.0,3.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,14,16,17,18,19,20,21,22,23,24,27,28,29,30,31,32,34,35,36,37,60,62,95,96],[14.0,1.0,1.0,29.0,1.0,10.0,1.0,1584.0,1.0,8.0,261.0,1.0,3.0,3.0,3.0,3.0,3.0,3.0,3.0,2.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,14,16,17,18,19,20,21,22,23,24,25,27,28,30,31,37,60,62,95,99],[14.0,1.0,1.0,29.0,1.0,10.0,1.0,2863.0,1.0,8.0,446.0,1.0,3.0,3.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,14,16,17,18,19,20,21,22,23,24,28,29,30,31,36,37,60,62,95,96],[14.0,5.0,1.0,29.0,1.0,10.0,1.0,1148.0,1.0,8.0,797.0,1.0,3.0,3.0,3.0,3.0,3.0,1.0,1.0,1.0,1.0,1.0]) 0 (110,[12,13,14,16,17,18,20,21,22,23,24,28,29,30,31,32,34,35,36,37,60,61,95,96],[14.0,6.0,1.0,29.0,1.0,10.0,602

### Save Only The Two Relevant Columns (label, features) in The Testing Set


> <br>

In [112]:
# Save the test data features1 and label only

criteoTestParquet = "/FileStore/test/criteofeatures_label_test_uncompressed.parquet"

(newTestData.coalesce(1).write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "uncompressed")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoTestParquet)               # Write DataFrame to parquet files
)

### Logestic Regression Model


> <br>

In [114]:
# logestic regression model
# fit the model on the train data

from pyspark.ml.classification import LogisticRegression

lr = (LogisticRegression()
      .setFeaturesCol('features')
      .setRegParam(0.0)
      .setLabelCol('label')
      .setMaxIter(10000))

ModelLR = lr.fit(criteoTrain)


critieoTestPredictions_lr = (ModelLR
                       .transform(criteoTest)
                       .cache())


### Saving The Logestic Regression Model


> <br>

In [116]:
import mleap.pyspark
from mleap.pyspark.spark_support import SimpleSparkSerializer

ModelLR.serializeToBundle("jar:file:/tmp/LR_model.zip", critieoTestPredictions_lr)

In [117]:
dbutils.fs.cp("file:/tmp/LR_model.zip", "dbfs:/FileStore/lr_model.zip")
display(dbutils.fs.ls("dbfs:/FileStore"))

path name size dbfs:/FileStore/jars/ jars/ 0 dbfs:/FileStore/lr_model.zip lr_model.zip 2152 dbfs:/FileStore/model_export/ model_export/ 0 dbfs:/FileStore/tables/ tables/ 0 dbfs:/FileStore/test/ test/ 0

In [118]:
display(critieoTestPredictions_lr)

label i_1 i_10 c_19 c_20 c_25 c_26 c_1_index c_2_index c_3_index c_4_index c_5_index c_6_index c_7_index c_8_index c_9_index c_10_index c_11_index c_12_index c_13_index c_14_index c_15_index c_16_index c_17_index c_18_index c_21_index c_23_index c_24_index i_2_bucket i_3_bucket i_4_bucket i_5_bucket i_6_bucket i_7_bucket i_8_bucket i_9_bucket i_11_bucket i_13_bucket c_6_OHE c_9_OHE c_14_OHE c_17_OHE c_23_OHE features rawPrediction probability prediction 0 false false false false false false 0 0 0 0 0 0 5 0 0 954 4 1 5 1 1401 1 2 450 1 0 0 3.0 0.0 1.0 3.0 3.0 3.0 2.0 3.0 2.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(1), List(1.0)) List(0, 9, List(2), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 27, 29, 30, 31, 32, 33, 34, 35, 36, 37, 59, 62, 89, 96), List(5.0, 954.0, 4.0, 1.0, 5.0, 1.0, 1401.0, 1.0, 2.0, 450.0, 1.0, 3.0, 1.0, 3.0, 3.0, 3.0, 2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.7493866476334627, -0.7493866476334627)) List(1, 2, List(), List(0.6790450380801913, 0.32095496191980866)) 0.0 0 false false false false false false 0 0 0 0 0 0 5 1 0 1476 4 1 5 0 588 1 0 82 1 0 0 2.0 3.0 0.0 3.0 3.0 0.0 0.0 3.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 30, 31, 34, 37, 59, 61, 87, 96), List(5.0, 1.0, 1476.0, 4.0, 1.0, 5.0, 588.0, 1.0, 82.0, 1.0, 2.0, 3.0, 3.0, 3.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(-0.12542943127978012, 0.12542943127978012)) List(1, 2, List(), List(0.46868368851795317, 0.5313163114820469)) 1.0 0 false false false false false false 0 0 0 0 0 0 5 2 0 141 4 1 5 0 6273 1 0 1486 1 0 0 0.0 0.0 3.0 1.0 2.0 0.0 3.0 1.0 0.0 2.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 29, 30, 31, 33, 34, 36, 37, 59, 61, 87, 96), List(5.0, 2.0, 141.0, 4.0, 1.0, 5.0, 6273.0, 1.0, 1486.0, 1.0, 3.0, 1.0, 2.0, 3.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.4055567810273656, -0.4055567810273656)) List(1, 2, List(), List(0.6000220012989006, 0.3999779987010994)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 0 0 65 5 1 8 2 977 1 0 687 1 0 0 1.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 0.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(2), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 23, 24, 27, 29, 31, 36, 37, 59, 63, 87, 96), List(6.0, 65.0, 5.0, 1.0, 8.0, 2.0, 977.0, 1.0, 687.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.6929106313128223, -0.6929106313128223)) List(1, 2, List(), List(0.6666140980950417, 0.3333859019049582)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 13 0 238 5 1 8 0 335 1 0 82 1 0 0 3.0 3.0 3.0 1.0 0.0 2.0 0.0 1.0 2.0 3.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 29, 30, 32, 34, 35, 36, 37, 59, 61, 87, 96), List(6.0, 13.0, 238.0, 5.0, 1.0, 8.0, 335.0, 1.0, 82.0, 1.0, 3.0, 3.0, 3.0, 1.0, 2.0, 1.0, 2.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(-0.6355677144371348, 0.6355677144371348)) List(1, 2, List(), List(0.34624914966214954, 0.6537508503378505)) 1.0 0 false false false false false false 0 0 0 0 0 0 9 0 0 108 17 1 16 0 1305 1 0 173 1 2 0 0.0 0.0 0.0 3.0 3.0 0.0 0.0 1.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(2), List(1.0)) List(0, 110, List(12, 15

### Random Forest model


> <br>

In [120]:
# Train a RandomForest model.

from pyspark.ml.classification import RandomForestClassifier
rf = RandomForestClassifier(labelCol="label", featuresCol="features", numTrees=50,maxDepth=25)

Modelrf = rf.fit(criteoTrain)


critieoTestPredictions_rf = (Modelrf
                       .transform(criteoTest)
                       .cache())

# default acc = 0.739
# numTrees=50, maxDepth=10  acc = 0.765
# numTrees=50, maxDepth=20 acc = 0.782
# numTrees=75, maxDepth=20  acc = 0.783
# numTrees=50, maxDepth=25  acc = crashed

In [121]:
# Random Forest Predictions
display(critieoTestPredictions_rf)

label i_1 i_10 c_19 c_20 c_25 c_26 c_1_index c_2_index c_3_index c_4_index c_5_index c_6_index c_7_index c_8_index c_9_index c_10_index c_11_index c_12_index c_13_index c_14_index c_15_index c_16_index c_17_index c_18_index c_21_index c_23_index c_24_index i_2_bucket i_3_bucket i_4_bucket i_5_bucket i_6_bucket i_7_bucket i_8_bucket i_9_bucket i_11_bucket i_13_bucket c_6_OHE c_9_OHE c_14_OHE c_17_OHE c_23_OHE features rawPrediction probability prediction 0 false false false false false false 0 0 0 0 0 0 5 0 0 954 4 1 5 1 1401 1 2 450 1 0 0 3.0 0.0 1.0 3.0 3.0 3.0 2.0 3.0 2.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(1), List(1.0)) List(0, 9, List(2), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 27, 29, 30, 31, 32, 33, 34, 35, 36, 37, 59, 62, 89, 96), List(5.0, 954.0, 4.0, 1.0, 5.0, 1.0, 1401.0, 1.0, 2.0, 450.0, 1.0, 3.0, 1.0, 3.0, 3.0, 3.0, 2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(6.5046313078031694, 3.4953686921968314)) List(1, 2, List(), List(0.6504631307803169, 0.34953686921968313)) 0.0 0 false false false false false false 0 0 0 0 0 0 5 1 0 1476 4 1 5 0 588 1 0 82 1 0 0 2.0 3.0 0.0 3.0 3.0 0.0 0.0 3.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 30, 31, 34, 37, 59, 61, 87, 96), List(5.0, 1.0, 1476.0, 4.0, 1.0, 5.0, 588.0, 1.0, 82.0, 1.0, 2.0, 3.0, 3.0, 3.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(6.7927323159568935, 3.2072676840431074)) List(1, 2, List(), List(0.6792732315956893, 0.32072676840431075)) 0.0 0 false false false false false false 0 0 0 0 0 0 5 2 0 141 4 1 5 0 6273 1 0 1486 1 0 0 0.0 0.0 3.0 1.0 2.0 0.0 3.0 1.0 0.0 2.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 29, 30, 31, 33, 34, 36, 37, 59, 61, 87, 96), List(5.0, 2.0, 141.0, 4.0, 1.0, 5.0, 6273.0, 1.0, 1486.0, 1.0, 3.0, 1.0, 2.0, 3.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(7.284974480038865, 2.7150255199611353)) List(1, 2, List(), List(0.7284974480038865, 0.2715025519961135)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 0 0 65 5 1 8 2 977 1 0 687 1 0 0 1.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 0.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(2), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 23, 24, 27, 29, 31, 36, 37, 59, 63, 87, 96), List(6.0, 65.0, 5.0, 1.0, 8.0, 2.0, 977.0, 1.0, 687.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(6.270480783175749, 3.7295192168242517)) List(1, 2, List(), List(0.6270480783175749, 0.3729519216824252)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 13 0 238 5 1 8 0 335 1 0 82 1 0 0 3.0 3.0 3.0 1.0 0.0 2.0 0.0 1.0 2.0 3.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 29, 30, 32, 34, 35, 36, 37, 59, 61, 87, 96), List(6.0, 13.0, 238.0, 5.0, 1.0, 8.0, 335.0, 1.0, 82.0, 1.0, 3.0, 3.0, 3.0, 1.0, 2.0, 1.0, 2.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(6.720240092321733, 3.279759907678267)) List(1, 2, List(), List(0.6720240092321733, 0.3279759907678267)) 0.0 0 false false false false false false 0 0 0 0 0 0 9 0 0 108 17 1 16 0 1305 1 0 173 1 2 0 0.0 0.0 0.0 3.0 3.0 0.0 0.0 1.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(2), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18

In [122]:
from pyspark.ml.tuning import ParamGridBuilder
from pyspark.ml.tuning import CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator
import numpy as np
from pyspark.ml.regression import RandomForestRegressor

rf = RandomForestRegressor(labelCol="label", featuresCol="features")

paramGrid = ParamGridBuilder() \
    .addGrid(rf.numTrees, [x for x in [50, 75] ]) \
    .addGrid(rf.maxDepth, [x for x in [20, 25] ]) \
    .build()


crossval = CrossValidator(estimator=rf,
                          estimatorParamMaps=paramGrid,
                          evaluator=RegressionEvaluator(),
                          numFolds=3)
cvModel = crossval.fit(criteoTrain)
predictions = cvModel.transform(criteoTest)

### Saving The Random Forest Model


> <br>

In [124]:
display(critieoTestPredictions_lr)

label i_1 i_10 c_19 c_20 c_25 c_26 c_1_index c_2_index c_3_index c_4_index c_5_index c_6_index c_7_index c_8_index c_9_index c_10_index c_11_index c_12_index c_13_index c_14_index c_15_index c_16_index c_17_index c_18_index c_21_index c_23_index c_24_index i_2_bucket i_3_bucket i_4_bucket i_5_bucket i_6_bucket i_7_bucket i_8_bucket i_9_bucket i_11_bucket i_13_bucket c_6_OHE c_9_OHE c_14_OHE c_17_OHE c_23_OHE features rawPrediction probability prediction 0 false false false false false false 0 0 0 0 0 0 5 0 0 954 4 1 5 1 1401 1 2 450 1 0 0 3.0 0.0 1.0 3.0 3.0 3.0 2.0 3.0 2.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(1), List(1.0)) List(0, 9, List(2), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 27, 29, 30, 31, 32, 33, 34, 35, 36, 37, 59, 62, 89, 96), List(5.0, 954.0, 4.0, 1.0, 5.0, 1.0, 1401.0, 1.0, 2.0, 450.0, 1.0, 3.0, 1.0, 3.0, 3.0, 3.0, 2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.7173743127045273, -0.7173743127045273)) List(1, 2, List(), List(0.6720285609933266, 0.3279714390066733)) 0.0 0 false false false false false false 0 0 0 0 0 0 5 1 0 1476 4 1 5 0 588 1 0 82 1 0 0 2.0 3.0 0.0 3.0 3.0 0.0 0.0 3.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 30, 31, 34, 37, 59, 61, 87, 96), List(5.0, 1.0, 1476.0, 4.0, 1.0, 5.0, 588.0, 1.0, 82.0, 1.0, 2.0, 3.0, 3.0, 3.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(-0.18590880730154985, 0.18590880730154985)) List(1, 2, List(), List(0.4536561995458742, 0.5463438004541258)) 1.0 0 false false false false false false 0 0 0 0 0 0 5 2 0 141 4 1 5 0 6273 1 0 1486 1 0 0 0.0 0.0 3.0 1.0 2.0 0.0 3.0 1.0 0.0 2.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 29, 30, 31, 33, 34, 36, 37, 59, 61, 87, 96), List(5.0, 2.0, 141.0, 4.0, 1.0, 5.0, 6273.0, 1.0, 1486.0, 1.0, 3.0, 1.0, 2.0, 3.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.319686795860182, -0.319686795860182)) List(1, 2, List(), List(0.5792479200039619, 0.4207520799960381)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 0 0 65 5 1 8 2 977 1 0 687 1 0 0 1.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 0.0 1.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(2), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 15, 16, 17, 18, 19, 20, 21, 23, 24, 27, 29, 31, 36, 37, 59, 63, 87, 96), List(6.0, 65.0, 5.0, 1.0, 8.0, 2.0, 977.0, 1.0, 687.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(0.7532738453829171, -0.7532738453829171)) List(1, 2, List(), List(0.6798916348474482, 0.32010836515255175)) 0.0 0 false false false false false false 0 0 0 0 0 0 6 13 0 238 5 1 8 0 335 1 0 82 1 0 0 3.0 3.0 3.0 1.0 0.0 2.0 0.0 1.0 2.0 3.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 110, List(12, 13, 15, 16, 17, 18, 20, 21, 23, 24, 27, 28, 29, 30, 32, 34, 35, 36, 37, 59, 61, 87, 96), List(6.0, 13.0, 238.0, 5.0, 1.0, 8.0, 335.0, 1.0, 82.0, 1.0, 3.0, 3.0, 3.0, 1.0, 2.0, 1.0, 2.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 2, List(), List(-0.7211316888704877, 0.7211316888704877)) List(1, 2, List(), List(0.32714382602375375, 0.6728561739762462)) 1.0 0 false false false false false false 0 0 0 0 0 0 9 0 0 108 17 1 16 0 1305 1 0 173 1 2 0 0.0 0.0 0.0 3.0 3.0 0.0 0.0 1.0 0.0 0.0 List(0, 22, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 26, List(0), List(1.0)) List(0, 9, List(0), List(1.0)) List(0, 14, List(2), List(1.0)) List(0, 110, List(12, 15, 1

In [125]:
import mleap.pyspark
from mleap.pyspark.spark_support import SimpleSparkSerializer

Modelrf.serializeToBundle("jar:file:/tmp/RF_model.zip", critieoTestPredictions_rf)

In [126]:
dbutils.fs.cp("file:/tmp/RF_model.zip", "dbfs:/FileStore/random_forest_model.zip")




Out[45]: True

### linearSVM model


> <br>

In [128]:
# training the data using a linearSVM model

from pyspark.ml.classification import LinearSVC
lsvc = LinearSVC(maxIter=20, regParam=0.1)

ModelLSVM = lsvc.fit(criteoTrain)


critieoTestPredictions_LSVM = (ModelLSVM
                       .transform(criteoTest)
                       .cache())

### Saving The SVM Model


> <br>

In [130]:
import mleap.pyspark
from mleap.pyspark.spark_support import SimpleSparkSerializer
# mleap.pyspark.mleap.version
ModelLSVM.serializeToBundle("jar:file:/tmp/LSVM_model.zip", critieoTestPredictions_LSVM)

In [131]:
dbutils.fs.cp("file:/tmp/LSVM_model.zip", "dbfs:/FileStore/lsvm_model.zip")

Out[9]: True

### Calculating Model Accuracies


> <br>

In [133]:
# model accuracy for logestic regression model
from pyspark.sql.functions import col

def modelAccuracy(df):
    return (df
          .select((col('prediction') == col('label')).cast('int').alias('correct'))
          .groupBy()
          .avg('correct')
          .first()[0])

modelAccuracy = modelAccuracy(critieoTestPredictions_lr)

print('modelOneAccuracy for the logestic regression model: {0:.3f}'.format(modelAccuracy))



In [134]:
# model accuracy for random forest model
from pyspark.sql.functions import col

def modelAccuracy(df):
    return (df
          .select((col('prediction') == col('label')).cast('int').alias('correct'))
          .groupBy()
          .avg('correct')
          .first()[0])

modelAccuracy = modelAccuracy(critieoTestPredictions_rf)
print('modelOneAccuracy for the Random Forest model: {0:.3f}'.format(modelAccuracy))



In [135]:
# model accuracy for linear SVM
from pyspark.sql.functions import col

def modelAccuracy(df):
    return (df
          .select((col('prediction') == col('label')).cast('int').alias('correct'))
          .groupBy()
          .avg('correct')
          .first()[0])

modelAccuracy = modelAccuracy(critieoTestPredictions_LSVM)

print('modelOneAccuracy for the LSVM model: {0:.3f}'.format(modelAccuracy))



modelOneAccuracy for the LSVM model: 0.702

In [136]:
# save the predictions
criteoPredictParquet = "/tmp/criteosmall_predict.parquet"

(critieoTestPredictions.write                       # Our DataFrameWriter
  .option("delimiter", "\t")  
  .option("compression", "snappy")
  .mode("overwrite")                       # Replace existing files
  .parquet(criteoPredictParquet)               # Write DataFrame to parquet files
)

In [137]:
# from mmlspark import LightGBMClassifier
# the above name space has changed

from mmlspark.lightgbm  import LightGBMClassifier
lgb_estimator = LightGBMClassifier(learningRate=0.1, 
                                   numIterations=100,
                                   earlyStoppingRound=10,
                                   labelCol="label", timeout=3000.0)

ModelLGB = lgb_estimator.fit(criteoTest)


critieoTestPredictions_LGBM = (ModelLGB
                       .transform(criteoTest)
                       .cache())

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 <command-1218978762911499> in <module> 
 8 labelCol="label", timeout=3000.0)
 9 
 ---> 10 ModelLGB = lgb_estimator . fit ( criteoTest ) 
 11 
 12 

 /databricks/spark/python/pyspark/ml/base.py in fit (self, dataset, params) 
 130 return self . copy ( params ) . _fit ( dataset ) 
 131 else : 
 --> 132 return self . _fit ( dataset ) 
 133 else : 
 134 raise ValueError("Params must be either a param map or a list/tuple of param maps, "

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit (self, dataset) 
 293 
 294 def _fit ( self , dataset ) : 
 --> 295 java_model = self . _fit_java ( dataset ) 
 296 model = self . _create_model ( java_model ) 
 297 return self . _copyValues ( model ) 

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit_java (self, dataset) 
 290 """
 291 self . _transfer_params_to_java ( ) 
 --> 292 return self . _java_obj . fit ( dataset . _jdf ) 
 293 
 294 def _fit ( self , dataset ) : 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1255 answer = self . gateway_client . send_command ( command ) 
 1256 return_value = get_return_value(
 -> 1257 answer, self.gateway_client, self.target_id, self.name)
 1258 
 1259 for temp_arg in temp_args : 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 61 def deco ( * a , ** kw ) : 
 62 try : 
 ---> 63 return f ( * a , ** kw ) 
 64 except py4j . protocol . Py4JJavaError as e : 
 65 s = e . java_exception . toString ( ) 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 326 raise Py4JJavaError(
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 --> 328 format(target_id, ".", name), value)
 329 else : 
 330 raise Py4JError(

 Py4JJavaError : An error occurred while calling o3652.fit.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 7 in stage 54.0 failed 4 times, most recent failure: Lost task 7.3 in stage 54.0 (TID 2312, 10.198.229.7, executor 55): java.net.ConnectException: Connection refused (Connection refused)
	at java.net.PlainSocketImpl.socketConnect(Native Method)
	at java.net.AbstractPlainSocketImpl.doConnect(AbstractPlainSocketImpl.java:350)
	at java.net.AbstractPlainSocketImpl.connectToAddress(AbstractPlainSocketImpl.java:206)
	at java.net.AbstractPlainSocketImpl.connect(AbstractPlainSocketImpl.java:188)
	at java.net.SocksSocketImpl.connect(SocksSocketImpl.java:392)
	at java.net.Socket.connect(Socket.java:607)
	at java.net.Socket.connect(Socket.java:556)
	at java.net.Socket.<init>(Socket.java:452)
	at java.net.Socket.<init>(Socket.java:229)
	at com.microsoft.ml.spark.lightgbm.TrainUtils$.getNetworkInitNodes(TrainUtils.scala:324)
	at com.microsoft.ml.spark.lightgbm.TrainUtils$$anonfun$15.apply(TrainUtils.scala:398)
	at com.microsoft.ml.spark.lightgbm.TrainUtils$$anonfun$15.apply(TrainUtils.scala:393)
	at com.microsoft.ml.spark.core.env.StreamUtilities$.using(StreamUtilities.scala:28)
	at com.microsoft.ml.spark.lightgbm.TrainUtils$.trainLightGBM(TrainUtils.scala:392)
	at com.microsoft.ml.spark.lightgbm.LightGBMBase$$anonfun$6.apply(LightGBMBase.scala:85)
	at com.microsoft.ml.spark.lightgbm.LightGBMBase$$anonfun$6.apply(LightGBMBase.scala:85)
	at org.apache.spark.sql.execution.MapPartitionsExec$$anonfun$5.apply(objects.scala:216)
	at org.apache.spark.sql.execution.MapPartitionsExec$$anonfun$5.apply(objects.scala:213)
	at org.apache.spark.rdd.RDD$$anonfun$mapPartitionsInternal$1$$anonfun$apply$24.apply(RDD.scala:865)
	at org.apache.spark.rdd.RDD$$anonfun$mapPartitionsInternal$1$$anonfun$apply$24.apply(RDD.scala:865)
	at org.apache.spark.rdd.MapPartitionsRDD.compute(MapPartitionsRDD.scala:60)
	at org.apache.spark.rdd.RDD.computeOrReadCheckpoint(RDD.scala:353)
	at org.apache.spark.rdd.RDD.iterator(RDD.scala:317)
	at org.apache.spark.sql.execution.SQLExecut

In [138]:
# search grid for tunning the logistic parameters values
from pyspark.ml import Pipeline
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
#logit = LogisticRegression(maxIter=10)
logit = (LogisticRegression()
      .setFeaturesCol('features')
      .setLabelCol('label')
      .setMaxIter(60))
pipeline = Pipeline(stages=[logit])
paramGrid = ParamGridBuilder() \
    .addGrid(logit.regParam, [0, 0.01, 0.05, 0.1, 0.5, 1.0,1.3,1.5,2.0]) \
    .addGrid(logit.elasticNetParam, [0.0, 0.1, 0.5, 0.8, 1]) \
    .build()
evaluator = BinaryClassificationEvaluator(metricName = 'areaUnderPR')
crossval = CrossValidator(estimator=pipeline,
                          estimatorParamMaps=paramGrid,
                          evaluator=evaluator,
                          numFolds=5)
tuned_model = crossval.fit(criteoTrain)
model = tuned_model.bestModel
critieoTestPredictions_lr = (model
                       .transform(criteoTest)
                       .cache())

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [139]:
# The End